In [1]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import xgboost as xgb
import lightgbm as lgb
import statsmodels.api as sm
import warnings
import shap
from sklearn.preprocessing import StandardScaler

from sklearn.preprocessing import MinMaxScaler
from sklearn.model_selection import StratifiedKFold
from pycaret.regression import *
from xgboost import XGBRegressor
from xgboost import XGBClassifier
from sklearn.tree import ExtraTreeClassifier
from sklearn.tree import ExtraTreeRegressor
from sklearn.experimental import enable_iterative_imputer 
from sklearn.impute import KNNImputer
from sklearn.impute import IterativeImputer
from sklearn.ensemble import GradientBoostingClassifier
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.tree import DecisionTreeClassifier
from sklearn.svm import SVC
from sklearn.preprocessing import MinMaxScaler
from sklearn.preprocessing import OneHotEncoder
from sklearn.preprocessing import LabelEncoder
from sklearn.model_selection import train_test_split
from sklearn.model_selection import GridSearchCV
from sklearn.model_selection import RandomizedSearchCV
from sklearn.ensemble import RandomForestClassifier
from sklearn.ensemble import RandomForestRegressor
from catboost import CatBoostClassifier, Pool
from sklearn.ensemble import AdaBoostClassifier
from sklearn.ensemble import AdaBoostRegressor
from catboost import CatBoostRegressor
from catboost import CatBoostClassifier
from sklearn.metrics import mean_squared_error
from sklearn.impute import KNNImputer

In [2]:
warnings.simplefilter(action='ignore')
pd.set_option('display.max_columns', None)

# Data

In [381]:
train_data = pd.read_csv("./train.csv")
train_data

PRODUCT_ID  Y_Class  Y_Quality         TIMESTAMP     LINE PRODUCT_CODE  \
0    TRAIN_000        1   0.533433   2022-06-13 5:14  T050304         A_31   
1    TRAIN_001        2   0.541819   2022-06-13 5:22  T050307         A_31   
2    TRAIN_002        1   0.531267   2022-06-13 5:30  T050304         A_31   
3    TRAIN_003        2   0.537325   2022-06-13 5:39  T050307         A_31   
4    TRAIN_004        1   0.531590   2022-06-13 5:47  T050304         A_31   
..         ...      ...        ...               ...      ...          ...   
593  TRAIN_593        1   0.526546  2022-09-08 14:30  T100306         T_31   
594  TRAIN_594        0   0.524022  2022-09-08 22:38  T050304         A_31   
595  TRAIN_595        0   0.521289  2022-09-08 22:47  T050304         A_31   
596  TRAIN_596        1   0.531375  2022-09-08 14:38  T100304         O_31   
597  TRAIN_597        1   0.533702  2022-09-08 14:46  T100306         O_31   

      X_1   X_2  X_3   X_4  ...  X_2866  X_2867  X_2868  X_2869  X_2870  \
0     NaN   NaN  NaN   NaN  ...   39.34   40.89   32.56   34.09   77.77   
1     NaN   NaN  NaN   NaN  ...   38.89   42.82   43.92   35.34   72.55   
2     NaN   NaN  NaN   NaN  ...   39.19   36.65   42.47   36.53   78.35   
3     NaN   NaN  NaN   NaN  ...   37.74   39.17   52.17   30.58   71.78   
4     NaN   NaN  NaN   NaN  ...   38.70   41.89   46.93   33.09   76.97   
..    ...   ...  ...   ...  ...     ...     ...     ...     ...     ...   
593   2.0  95.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
594   NaN   NaN  NaN   NaN  ...   49.47   53.07   50.89   55.10   66.49   
595   NaN   NaN  NaN   NaN  ...     NaN     NaN     NaN     NaN     NaN   
596  40.0  94.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   
597  21.0  87.0  0.0  45.0  ...     NaN     NaN     NaN     NaN     NaN   

     X_2871  X_2872  X_2873  X_2874  X_2875  
0       NaN     NaN     NaN     NaN     NaN  
1       NaN     NaN     NaN     NaN     NaN  
2       NaN     NaN     NaN     NaN     NaN  
3       NaN     NaN     NaN     NaN     NaN  
4       NaN     NaN     NaN     NaN     NaN  
..      ...     ...     ...     ...     ...  
593     NaN     NaN     NaN     NaN     NaN  
594     1.0     NaN     NaN     NaN     NaN  
595     1.0     NaN     NaN     NaN     NaN  
596     NaN     NaN     NaN     NaN     NaN  
597     NaN     NaN     NaN     NaN     NaN  

[598 rows x 2881 columns]

In [382]:
colls = []
for coll in train_data :
    if 'X' in coll and train_data[coll].isna().sum() == 598 :
        colls.append(coll)
print(len(colls))

82


In [383]:
train_data.drop(colls, inplace = True, axis = 1)

In [384]:
train_data.loc[train_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
train_data.loc[train_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
train_data.loc[train_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

train_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
train_data

Y_Class  Y_Quality     LINE PRODUCT_CODE   X_1   X_2  X_3   X_4   X_5  \
0          1   0.533433  T050304            1   NaN   NaN  NaN   NaN   NaN   
1          2   0.541819  T050307            1   NaN   NaN  NaN   NaN   NaN   
2          1   0.531267  T050304            1   NaN   NaN  NaN   NaN   NaN   
3          2   0.537325  T050307            1   NaN   NaN  NaN   NaN   NaN   
4          1   0.531590  T050304            1   NaN   NaN  NaN   NaN   NaN   
..       ...        ...      ...          ...   ...   ...  ...   ...   ...   
593        1   0.526546  T100306            2   2.0  95.0  0.0  45.0  10.0   
594        0   0.524022  T050304            1   NaN   NaN  NaN   NaN   NaN   
595        0   0.521289  T050304            1   NaN   NaN  NaN   NaN   NaN   
596        1   0.531375  T100304            3  40.0  94.0  0.0  45.0  11.0   
597        1   0.533702  T100306            3  21.0  87.0  0.0  45.0  10.0   

     X_6  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  \
0    NaN  ...   189.0   383.0  368.296296   353.0   39.34   40.89   32.56   
1    NaN  ...   185.6   383.0  367.735849   353.0   38.89   42.82   43.92   
2    NaN  ...   165.5   383.0  367.320755   353.0   39.19   36.65   42.47   
3    NaN  ...   165.8   384.0  369.188679   353.0   37.74   39.17   52.17   
4    NaN  ...   182.6   383.0  367.351852   352.0   38.70   41.89   46.93   
..   ...  ...     ...     ...         ...     ...     ...     ...     ...   
593  0.0  ...     NaN     NaN         NaN     NaN     NaN     NaN     NaN   
594  NaN  ...   168.7   384.0  369.811321   353.0   49.47   53.07   50.89   
595  NaN  ...   156.6   383.0  367.018868   352.0     NaN     NaN     NaN   
596  0.0  ...     NaN     NaN         NaN     NaN     NaN     NaN     NaN   
597  0.0  ...     NaN     NaN         NaN     NaN     NaN     NaN     NaN   

     X_2869  X_2870  X_2871  
0     34.09   77.77     NaN  
1     35.34   72.55     NaN  
2     36.53   78.35     NaN  
3     30.58   71.78     NaN  
4     33.09   76.97     NaN  
..      ...     ...     ...  
593     NaN     NaN     NaN  
594   55.10   66.49     1.0  
595     NaN     NaN     1.0  
596     NaN     NaN     NaN  
597     NaN     NaN     NaN  

[598 rows x 2797 columns]

In [385]:
T05 = train_data[(train_data['LINE'] == 'T050304')|(train_data['LINE'] == 'T050307')]
T01 = train_data[(train_data['LINE'] == 'T010305')|(train_data['LINE'] == 'T010306')]
T10 = train_data[(train_data['LINE'] == 'T100304')|(train_data['LINE'] == 'T100306')]

In [386]:
T05.drop(['LINE'], axis = 1, inplace = True)
T01.drop(['LINE'], axis = 1, inplace = True)
T10.drop(['LINE'], axis = 1, inplace = True)

In [387]:
T05_col = []
for col in T05 :
    if 'X' in col and T05[col].isna().sum() == len(T05) :
        T05_col.append(col)
print(len(T05_col))

T05.drop(T05_col, inplace = True, axis = 1)

806


In [388]:
T01_col = []
for col in T01 :
    if 'X' in col and T01[col].isna().sum() == len(T01) :
        T01_col.append(col)
print(len(T01_col))

T01.drop(T01_col, inplace = True, axis = 1)

1899


In [389]:
T10_col = []
for col in T10 :
    if 'X' in col and T10[col].isna().sum() == len(T10) :
        T10_col.append(col)
print(len(T10_col))

T10.drop(T10_col, inplace = True, axis = 1)

2116


In [390]:
T05 = T05.fillna(0)
T01 = T01.fillna(0)
T10 = T10.fillna(0)

# T05

In [391]:
T05_class = T05['Y_Class']
T05_target = T05['Y_Quality']
T05_data = T05.drop(['Y_Class', 'Y_Quality'], axis = 1)
T05_data
T05_target

0      0.533433
1      0.541819
2      0.531267
3      0.537325
4      0.531590
         ...   
581    0.523465
582    0.522233
583    0.522340
594    0.524022
595    0.521289
Name: Y_Quality, Length: 120, dtype: float64

In [14]:
T_05c = T05_data.columns
T_05scaler = StandardScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
0             0.0 -0.180370 -0.186560 -0.509145 -0.509145 -1.164247 -1.497746   
1             0.0 -0.989393 -0.995545  2.139491  2.139491  0.803495  0.667670   
2             0.0 -0.180163 -0.186353 -0.509145 -0.509145 -1.164247 -1.497746   
3             0.0 -0.989393 -0.995545  2.139758  2.139758  0.803495  0.667670   
4             0.0 -0.179956 -0.186145 -0.509145 -0.509145 -1.164247 -1.497746   
..            ...       ...       ...       ...       ...       ...       ...   
115           0.0  0.239104  0.232895 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
117           0.0  0.244903  0.238694 -0.509145 -0.509145 -1.164247 -1.497746   
118           0.0  0.544158  0.537935 -0.509145 -0.509145 -1.164247 -1.497746   
119           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   

        X_134         X_135     X_136     X_137     X_138     X_139     X_140  \
0   -0.912871 -2.775558e-17 -0.604357 -0.605226 -0.614824  0.007339 -0.068550   
1    0.912871 -2.775558e-17  0.076557  0.079866  0.080717  0.493205  0.547338   
2   -0.912871 -2.775558e-17 -0.604357 -0.605226 -0.614824  0.075664 -0.033154   
3    0.912871 -2.775558e-17  0.080237  0.079866  0.080717  0.531163  0.568576   
4   -2.738613 -2.775558e-17 -0.604357 -0.605226 -0.614824  0.030114 -0.054392   
..        ...           ...       ...       ...       ...       ...       ...   
115 -0.912871 -2.775558e-17 -0.596995 -0.597860 -0.596423  0.090847  0.044717   
116 -2.738613 -2.775558e-17 -0.596995 -0.597860 -0.596423  0.037705  0.023479   
117 -0.912871 -2.775558e-17 -0.596995 -0.597860 -0.596423  0.052889  0.016400   
118 -0.912871 -2.775558e-17 -0.324630 -0.325296 -0.324095  0.462838  0.462388   
119 -0.912871 -2.775558e-17 -0.324630 -0.325296 -0.324095  0.455247  0.462388   

        X_141  X_142    X_143     X_144         X_145     X_146  X_147  \
0    0.153163    0.0 -0.09167 -0.515457  1.136868e-13  0.342590    0.0   
1    0.717882    0.0 -0.09167  0.829213  1.136868e-13  0.907637    0.0   
2    0.520887    0.0 -0.09167  0.829213  1.136868e-13  0.812984    0.0   
3   -0.181728    0.0 -0.09167  0.829213  1.136868e-13 -0.862079    0.0   
4    0.061233    0.0 -0.09167 -0.515457  1.136868e-13  0.055764    0.0   
..        ...    ...      ...       ...           ...       ...    ...   
115 -0.444387    0.0 -0.09167 -0.515457  1.136868e-13 -1.447204    0.0   
116  0.337025    0.0 -0.09167 -0.515457  1.136868e-13  0.529027    0.0   
117 -0.595417    0.0 -0.09167  0.829213  1.136868e-13 -1.593485    0.0   
118  0.645650    0.0 -0.09167  0.829213  1.136868e-13  0.437242    0.0   
119  0.382991    0.0 -0.09167 -0.515457  1.136868e-13 -0.188038    0.0   

        X_148     X_149     X_150     X_151     X_152     X_153  X_154  \
0   -0.046493 -0.114375  0.083216 -1.268344 -0.255393  0.651615    0.0   
1   -0.553692 -0.319227 -0.595442 -1.268344 -0.255393 -1.255551    0.0   
2   -0.147933 -0.216801 -0.013735 -1.268344 -0.255393 -1.255551    0.0   
3   -0.553692 -0.319227 -0.595442 -1.268344 -0.255393  0.651615    0.0   
4   -0.046493 -0.216801  0.083216  0.788430 -0.255393 -1.255551    0.0   
..        ...       ...       ...       ...       ...       ...    ...   
115 -0.147933 -0.216801 -0.110686  0.788430 -0.255393  0.651615    0.0   
116 -0.046493  0.090476 -0.013735  0.788430 -0.255393  0.651615    0.0   
117 -0.046493 -0.114375 -0.013735  0.788430 -0.255393  0.651615    0.0   
118 -0.452252 -0.524078 -0.498491 -1.268344 -0.255393  0.651615    0.0   
119 -0.452252 -0.524078 -0.498491  0.788430 -0.255393  0.651615    0.0   

        X_155     X_156     X_157  X_158     X_159  X_160     X_161  X_162  \
0    0.667670 -0.422577 -0.111386    0.0 -1.051315   -0.5 -0.300543    0.0   
1   -1.497746  2.112886 -2.784662    0.0 -1.051315   -0.5 -0.300543    0.0   
2    0.667670 -0.422577 -0.111386    0.0  0.951

In [15]:
T05_y_class = pd.DataFrame(T05_target, columns = ['Y_Quality'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_data = pd.concat([T05_data, T05_y_class], axis = 1)
T05_data = T05_data.set_index('index')
T05_data.drop(['Y_Quality'], axis = 1, inplace = True)
T05_data

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132  \
index                                                                   
0               0.0 -0.180370 -0.186560 -0.509145 -0.509145 -1.164247   
1               0.0 -0.989393 -0.995545  2.139491  2.139491  0.803495   
2               0.0 -0.180163 -0.186353 -0.509145 -0.509145 -1.164247   
3               0.0 -0.989393 -0.995545  2.139758  2.139758  0.803495   
4               0.0 -0.179956 -0.186145 -0.509145 -0.509145 -1.164247   
...             ...       ...       ...       ...       ...       ...   
581             0.0  0.239104  0.232895 -0.509145 -0.509145 -1.164247   
582             0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989   
583             0.0  0.244903  0.238694 -0.509145 -0.509145 -1.164247   
594             0.0  0.544158  0.537935 -0.509145 -0.509145 -1.164247   
595             0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247   

          X_133     X_134         X_135     X_136     X_137     X_138  \
index                                                                   
0     -1.497746 -0.912871 -2.775558e-17 -0.604357 -0.605226 -0.614824   
1      0.667670  0.912871 -2.775558e-17  0.076557  0.079866  0.080717   
2     -1.497746 -0.912871 -2.775558e-17 -0.604357 -0.605226 -0.614824   
3      0.667670  0.912871 -2.775558e-17  0.080237  0.079866  0.080717   
4     -1.497746 -2.738613 -2.775558e-17 -0.604357 -0.605226 -0.614824   
...         ...       ...           ...       ...       ...       ...   
581   -1.497746 -0.912871 -2.775558e-17 -0.596995 -0.597860 -0.596423   
582   -1.497746 -2.738613 -2.775558e-17 -0.596995 -0.597860 -0.596423   
583   -1.497746 -0.912871 -2.775558e-17 -0.596995 -0.597860 -0.596423   
594   -1.497746 -0.912871 -2.775558e-17 -0.324630 -0.325296 -0.324095   
595   -1.497746 -0.912871 -2.775558e-17 -0.324630 -0.325296 -0.324095   

          X_139     X_140     X_141  X_142    X_143     X_144         X_145  \
index                                                                         
0      0.007339 -0.068550  0.153163    0.0 -0.09167 -0.515457  1.136868e-13   
1      0.493205  0.547338  0.717882    0.0 -0.09167  0.829213  1.136868e-13   
2      0.075664 -0.033154  0.520887    0.0 -0.09167  0.829213  1.136868e-13   
3      0.531163  0.568576 -0.181728    0.0 -0.09167  0.829213  1.136868e-13   
4      0.030114 -0.054392  0.061233    0.0 -0.09167 -0.515457  1.136868e-13   
...         ...       ...       ...    ...      ...       ...           ...   
581    0.090847  0.044717 -0.444387    0.0 -0.09167 -0.515457  1.136868e-13   
582    0.037705  0.023479  0.337025    0.0 -0.09167 -0.515457  1.136868e-13   
583    0.052889  0.016400 -0.595417    0.0 -0.09167  0.829213  1.136868e-13   
594    0.462838  0.462388  0.645650    0.0 -0.09167  0.829213  1.136868e-13   
595    0.455247  0.462388  0.382991    0.0 -0.09167 -0.515457  1.136868e-13   

          X_146  X_147     X_148     X_149     X_150     X_151     X_152  \
index                                                                      
0      0.342590    0.0 -0.046493 -0.114375  0.083216 -1.268344 -0.255393   
1      0.907637    0.0 -0.553692 -0.319227 -0.595442 -1.268344 -0.255393   
2      0.812984    0.0 -0.147933 -0.216801 -0.013735 -1.268344 -0.255393   
3     -0.862079    0.0 -0.553692 -0.319227 -0.595442 -1.268344 -0.255393   
4      0.055764    0.0 -0.046493 -0.216801  0.083216  0.788430 -0.255393   
...         ...    ...       ...       ...       ...       ...       ...   
581   -1.447204    0.0 -0.147933 -0.216801 -0.110686  0.788430 -0.255393   
582    0.529027    0.0 -0.046493  0.090476 -0.013735  0.788430 -0.255393   
583   -1.593485    0.0 -0.046493 -0.114375 -0.013735  0.788430 -0.255393   
594    0.437242    0.0 -0.452252 -0.524078 -0.498491 -1.268344 -0.255393   
595   -0.188038    0.0 -0.452252 -0.524078 -0.498491  0.788430 -0.255393   

          X_153  X_154     X_155     X_156     X_157  X_158     X_159  X_160  \
index     

In [16]:
#13
setup_rgs = setup(data = T05_data, target = T05_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [17]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbr = create_model('gbr', fold = 5)
T05_total_models.append(T05_model_gbr)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [18]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbr = tune_model(T05_model_gbr, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [19]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbr, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMRegressor(random_state=414),
 RandomForestRegressor(n_jobs=-1, random_state=414),
 GradientBoostingRegressor(random_state=414),
 ExtraTreesRegressor(n_jobs=-1, random_state=414),
 XGBRegressor(base_score=0.5, booster='gbtree', callbacks=None,
              colsample_bylevel=1, colsample_bynode=1, colsample_bytree=1,
              early_stopping_rounds=None, enable_categorical=False,
              eval_metric=None, gamma=0, gpu_id=-1, grow_policy='depthwise',
              importance_type=None, interaction_constraints='',
              learning_rate=0.300000012, max_bin=256, max_cat_to_onehot=4,
              max_delta_step=0, max_depth=6, max_leaves=0, min_child_weight=1,
              missing=nan, monotone_constraints='()', n_estimators=100,
              n_jobs=-1, num_parallel_tree=1, predictor='auto', random_state=414,
              reg_alpha=0, reg_lambda=1, ...),
 AdaBoostRegressor(random_state=414)]

In [20]:
for model in T05_tuned_models:
    display(predict_model(model))

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
84            0.0 -0.623039 -0.629208 -0.509145 -0.509145  0.803495  0.667670   
85            0.0 -0.989393 -0.995545 -0.398552 -0.398552 -1.164247 -1.497746   
86            0.0  1.542156  1.535887 -0.509145 -0.509145 -1.164247  0.667670   
87            0.0  0.229578  0.223369 -0.509145 -0.509145 -1.164247 -1.497746   
88            0.0  1.632761  1.626488 -0.509145 -0.509145  0.803495  0.667670   
89            0.0  0.816593  0.810358 -0.509145 -0.509145  0.803495  0.667670   
90            0.0  0.226575  0.220367 -0.509145 -0.509145  0.803495  0.667670   
91            0.0 -0.989393 -0.995545  0.354390  0.354390  0.803495  0.667670   
92            0.0 -0.989393 -0.995545 -0.300899 -0.300899  0.803495  0.667670   
93            0.0 -0.684236 -0.690403 -0.509145 -0.509145  0.803495  0.667670   
94            0.0 -0.989393 -0.995545  2.141092  2.141092  0.803495  0.667670   
95            0.0 -0.989393 -0.995545  0.355591  0.355591  0.803495  0.667670   
96            0.0 -0.989393 -0.995545  2.139492  2.139492  0.803495  0.667670   
97            0.0  1.443061  1.436796 -0.509145 -0.509145  0.803495  0.667670   
98            0.0 -0.139572 -0.145763 -0.509145 -0.509145 -1.164247 -1.497746   
99            0.0  1.274484  1.268227 -0.509145 -0.509145  0.803495  0.667670   
100           0.0 -0.902723 -0.908879 -0.509145 -0.509145 -1.164247 -1.497746   
101           0.0  0.986102  0.979859 -0.509145 -0.509145  0.803495  0.667670   
102           0.0 -0.989393 -0.995545 -0.386545 -0.386545 -1.164247  0.667670   
103           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
104           0.0 -0.989393 -0.995545  2.142426  2.142426  0.803495  0.667670   
105           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   
106           0.0  1.571150  1.564880 -0.509145 -0.509145  0.803495 -1.497746   
107           0.0  1.764578  1.758299 -0.509145 -0.509145  0.803495  0.667670   
108           0.0  0.983824  0.977581 -0.509145 -0.509145  0.803495  0.667670   
109           0.0 -0.415839 -0.422018 -0.509145 -0.509145 -1.164247 -1.497746   
110           0.0  1.327708  1.321449 -0.509145 -0.509145  0.803495  0.667670   
111           0.0  0.227093  0.220884 -0.509145 -0.509145 -1.164247 -1.497746   
112           0.0 -0.685789 -0.691956 -0.509145 -0.509145  0.803495  0.667670   
113           0.0 -0.989393 -0.995545  2.980081  2.980081  0.803495  0.667670   
114           0.0 -0.989393 -0.995545  1.083986  1.083986  0.803495  0.667670   
115           0.0 -0.178610 -0.184799 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0 -0.989393 -0.995545  2.140826  2.140826  0.803495  0.667670   
117           0.0  1.587200  1.580929 -0.509145 -0.509145  0.803495  0.667670   
118           0.0 -0.989393 -0.995545  2.330929  2.330929  0.803495  0.667670   
119           0.0 -0.989393 -0.995545 -0.401620 -0.401620 -1.164247  0.667670   

        X_134         X_135     X_136  ...    X_2864    X_2865    X_2866  \
84   0.912871 -2.775558e-17 -1.049711  ... -1.478055 -2.575510  0.372955   
85  -0.912871 -2.775558e-17 -1.230061  ... -0.009696  0.203817  0.438530   
86  -0.912871 -2.775558e-17  1.541441  ... -0.130254  0.203817  0.610226   
87  -0.912871 -2.775558e-17 -0.604357  ...  0.934679  0.481750  0.242806   
88   0.912871 -2.775558e-17  0.959904  ...  0.308666  0.203817  0.558167   
89   0.912871 -2.775558e-17  0.658094  ...  0.204711  0.203817  0.896052   
90  -0.912871 -2.775558e-17  0.106002  ... -0.264168  0.203817 -2.119391   
91   0.912871 -2.775558e-17 -0.814152  ...  0.490586  0.481750  0.853003   
92   0.912871 -2.775558e-17 -1.196936  ...  0.146236  0.481750 -2.119391   
93  -0.912871 -2.775558e-17 -0.990821  ... -0.074667  0.203817  0.297369   
94   0.912871 -2.775558e-17  0.080237  ...  2.235556  0.203817 -0.159153   
95   0.912871 -2.775558e-17 -0.810471  ... -0.087662  0.203817 -2.119391   
96   0.912871 -2.77

In [21]:
T05_final_regression_model = finalize_model(T05_model_gbr)

In [22]:
T05_prediction = predict_model(T05_final_regression_model, data=T05_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [41]:
T05_datas = T05_prediction['prediction_label']
T05_datas = pd.DataFrame(T05_datas.values, columns = ['Y_Quality'])
T05_datas

Y_Quality
0     0.533277
1     0.541837
2     0.531457
3     0.537330
4     0.531651
..         ...
115   0.523485
116   0.522365
117   0.522453
118   0.523849
119   0.521306

[120 rows x 1 columns]

In [42]:
T05y_idx= T05_class.index
T05y_idx = pd.DataFrame(T05y_idx, columns = ['index'])
T05_datas = pd.concat([T05y_idx, T05_datas], axis = 1)
T05_datas = T05_datas.set_index('index')
T05_datas

Y_Quality
index           
0       0.533277
1       0.541837
2       0.531457
3       0.537330
4       0.531651
...          ...
581     0.523485
582     0.522365
583     0.522453
594     0.523849
595     0.521306

[120 rows x 1 columns]

In [43]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T05_datas, 
                   target=T05_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [44]:
T05_total_models = []

T05_model_lightgbm = create_model('lightgbm', fold = 5)
T05_total_models.append(T05_model_lightgbm)

T05_model_rf = create_model('rf', fold = 5)
T05_total_models.append(T05_model_rf)

T05_model_gbc = create_model('gbc', fold = 5)
T05_total_models.append(T05_model_gbc)

T05_model_et = create_model('et', fold = 5)
T05_total_models.append(T05_model_et)

T05_model_catboost = create_model('catboost', fold = 5)
T05_total_models.append(T05_model_catboost)

T05_model_xgb = create_model('xgboost', fold = 5)
T05_total_models.append(T05_model_xgb)

T05_model_ada = create_model('ada', fold = 5)

T05_total_models.append(T05_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [45]:
T05_model_lightgbm = tune_model(T05_model_lightgbm, fold=5, choose_better = True)

T05_model_rf = tune_model(T05_model_rf, fold=5, choose_better = True)

T05_model_gbc = tune_model(T05_model_gbc, fold=5, choose_better = True)

T05_model_et = tune_model(T05_model_et, fold=5, choose_better = True)

T05_model_catboost = tune_model(T05_model_catboost, fold=5, choose_better = True)

T05_model_xgb = tune_model(T05_model_xgb, fold=5, choose_better = True)

T05_model_ada = tune_model(T05_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [46]:
T05_tuned_models = [T05_model_lightgbm, T05_model_rf, T05_model_gbc, T05_model_et, T05_model_catboost, T05_model_xgb, T05_model_ada]
T05_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp

In [47]:
for model in T05_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 0            0.6880
85    0.521529        0                 0            0.9920
86    0.525425        1                 1            0.9946
87    0.519527        0                 0            0.9920
88    0.541366        2                 2            0.9903
89    0.521132        0                 0            0.9920
90    0.528344        1                 1            0.9956
91    0.541837        2                 2            0.9903
92    0.525148        1                 0            0.6880
93    0.531398        1                 1            0.9954
94    0.517521        0                 0            0.9920
95    0.539820        2                 2            0.9903
96    0.531869        1                 1            0.9954
97    0.527900        1                 1            0.9956
98    0.539170        2                 2            0.9903
99    0.527346        1                 1            0.9956
100   0.531541        1                 1            0.9954
101   0.543884        2                 2            0.9903
102   0.540019        2                 2            0.9903
103   0.523849        0                 0            0.9920
104   0.531755        1                 1            0.9954
105   0.524721        0                 0            0.6880
106   0.550357        2                 2            0.9903
107   0.533475        1                 1            0.9917
108   0.515950        0                 0            0.9920
109   0.559453        2                 2            0.9903
110   0.538482        2                 2            0.9903
111   0.521503        0                 0            0.9920
112   0.523485        0                 0            0.9920
113   0.524866        0                 0            0.6880
114   0.523941        0                 0            0.9920
115   0.531457        1                 1            0.9954
116   0.533922        1                 1            0.9917
117   0.532194        1                 1            0.9950
118   0.531352        1                 1            0.9954
119   0.560452        2                 2            0.9903

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 1              0.73
85    0.521529        0                 0              1.00
86    0.525425        1                 1              0.85
87    0.519527        0                 0              1.00
88    0.541366        2                 2              1.00
89    0.521132        0                 0              1.00
90    0.528344        1                 1              1.00
91    0.541837        2                 2              1.00
92    0.525148        1                 1              0.84
93    0.531398        1                 1              1.00
94    0.517521        0                 0              1.00
95    0.539820        2                 2              1.00
96    0.531869        1                 1              1.00
97    0.527900        1                 1              1.00
98    0.539170        2                 2              1.00
99    0.527346        1                 1              1.00
100   0.531541        1                 1              1.00
101   0.543884        2                 2              1.00
102   0.540019        2                 2              1.00
103   0.523849        0                 0              0.98
104   0.531755        1                 1              1.00
105   0.524721        0                 0              0.86
106   0.550357        2                 2              1.00
107   0.533475        1                 1              1.00
108   0.515950        0                 0              1.00
109   0.559453        2                 2              1.00
110   0.538482        2                 2              1.00
111   0.521503        0                 0              1.00
112   0.523485        0                 0              1.00
113   0.524866        0                 0              0.68
114   0.523941        0                 0              0.98
115   0.531457        1                 1              1.00
116   0.533922        1                 1              1.00
117   0.532194        1                 1              1.00
118   0.531352        1                 1              1.00
119   0.560452        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 1            0.9390
85    0.521529        0                 0            0.9997
86    0.525425        1                 1            0.9965
87    0.519527        0                 0            0.9997
88    0.541366        2                 2            0.9997
89    0.521132        0                 0            0.9997
90    0.528344        1                 1            0.9998
91    0.541837        2                 2            0.9997
92    0.525148        1                 1            0.9941
93    0.531398        1                 1            0.9998
94    0.517521        0                 0            0.9997
95    0.539820        2                 2            0.9997
96    0.531869        1                 1            0.9998
97    0.527900        1                 1            0.9998
98    0.539170        2                 2            0.9997
99    0.527346        1                 1            0.9998
100   0.531541        1                 1            0.9998
101   0.543884        2                 2            0.9997
102   0.540019        2                 2            0.9997
103   0.523849        0                 0            0.9976
104   0.531755        1                 1            0.9998
105   0.524721        0                 0            0.9863
106   0.550357        2                 2            0.9997
107   0.533475        1                 1            0.9998
108   0.515950        0                 0            0.9997
109   0.559453        2                 2            0.9997
110   0.538482        2                 2            0.9997
111   0.521503        0                 0            0.9997
112   0.523485        0                 0            0.9997
113   0.524866        0                 0            0.8778
114   0.523941        0                 0            0.9976
115   0.531457        1                 1            0.9998
116   0.533922        1                 1            0.9998
117   0.532194        1                 1            0.9998
118   0.531352        1                 1            0.9998
119   0.560452        2                 2            0.9997

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 1            0.4027
85    0.521529        0                 0            0.5177
86    0.525425        1                 1            0.4129
87    0.519527        0                 0            0.5539
88    0.541366        2                 2            0.5334
89    0.521132        0                 0            0.5288
90    0.528344        1                 1            0.4684
91    0.541837        2                 2            0.5358
92    0.525148        1                 1            0.4066
93    0.531398        1                 1            0.4352
94    0.517521        0                 0            0.5657
95    0.539820        2                 2            0.5210
96    0.531869        1                 1            0.4273
97    0.527900        1                 1            0.4649
98    0.539170        2                 2            0.5013
99    0.527346        1                 1            0.4631
100   0.531541        1                 1            0.4335
101   0.543884        2                 2            0.5510
102   0.540019        2                 2            0.5253
103   0.523849        0                 0            0.4564
104   0.531755        1                 1            0.4273
105   0.524721        0                 0            0.4044
106   0.550357        2                 2            0.5728
107   0.533475        1                 1            0.3921
108   0.515950        0                 0            0.5657
109   0.559453        2                 2            0.5728
110   0.538482        2                 2            0.4980
111   0.521503        0                 0            0.5177
112   0.523485        0                 0            0.4715
113   0.524866        0                 1            0.3902
114   0.523941        0                 0            0.4487
115   0.531457        1                 1            0.4352
116   0.533922        1                 1            0.3901
117   0.532194        1                 1            0.4194
118   0.531352        1                 1            0.4387
119   0.560452        2                 2            0.5728

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 1            0.9818
85    0.521529        0                 0            0.9991
86    0.525425        1                 1            0.9908
87    0.519527        0                 0            0.9990
88    0.541366        2                 2            0.9987
89    0.521132        0                 0            0.9991
90    0.528344        1                 1            0.9992
91    0.541837        2                 2            0.9987
92    0.525148        1                 1            0.9818
93    0.531398        1                 1            0.9991
94    0.517521        0                 0            0.9989
95    0.539820        2                 2            0.9988
96    0.531869        1                 1            0.9990
97    0.527900        1                 1            0.9991
98    0.539170        2                 2            0.9988
99    0.527346        1                 1            0.9991
100   0.531541        1                 1            0.9990
101   0.543884        2                 2            0.9988
102   0.540019        2                 2            0.9988
103   0.523849        0                 0            0.9964
104   0.531755        1                 1            0.9990
105   0.524721        0                 0            0.9772
106   0.550357        2                 2            0.9986
107   0.533475        1                 1            0.9978
108   0.515950        0                 0            0.9988
109   0.559453        2                 2            0.9983
110   0.538482        2                 2            0.9988
111   0.521503        0                 0            0.9991
112   0.523485        0                 0            0.9964
113   0.524866        0                 0            0.9772
114   0.523941        0                 0            0.9964
115   0.531457        1                 1            0.9991
116   0.533922        1                 1            0.9926
117   0.532194        1                 1            0.9989
118   0.531352        1                 1            0.9991
119   0.560452        2                 2            0.9983

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 1            0.9773
85    0.521529        0                 0            0.9840
86    0.525425        1                 1            0.9773
87    0.519527        0                 0            0.9840
88    0.541366        2                 2            0.9803
89    0.521132        0                 0            0.9840
90    0.528344        1                 1            0.9888
91    0.541837        2                 2            0.9803
92    0.525148        1                 1            0.9773
93    0.531398        1                 1            0.9810
94    0.517521        0                 0            0.9840
95    0.539820        2                 2            0.9803
96    0.531869        1                 1            0.9810
97    0.527900        1                 1            0.9824
98    0.539170        2                 2            0.9803
99    0.527346        1                 1            0.9817
100   0.531541        1                 1            0.9810
101   0.543884        2                 2            0.9803
102   0.540019        2                 2            0.9803
103   0.523849        0                 0            0.9840
104   0.531755        1                 1            0.9810
105   0.524721        0                 0            0.9840
106   0.550357        2                 2            0.9803
107   0.533475        1                 1            0.9784
108   0.515950        0                 0            0.9840
109   0.559453        2                 2            0.9803
110   0.538482        2                 2            0.9803
111   0.521503        0                 0            0.9840
112   0.523485        0                 0            0.9840
113   0.524866        0                 0            0.9840
114   0.523941        0                 0            0.9840
115   0.531457        1                 1            0.9810
116   0.533922        1                 1            0.9784
117   0.532194        1                 1            0.9810
118   0.531352        1                 1            0.9810
119   0.560452        2                 2            0.9803

Y_Quality  Y_Class  prediction_label  prediction_score
84    0.525083        0                 1               1.0
85    0.521529        0                 0               1.0
86    0.525425        1                 1               1.0
87    0.519527        0                 0               1.0
88    0.541366        2                 2               1.0
89    0.521132        0                 0               1.0
90    0.528344        1                 1               1.0
91    0.541837        2                 2               1.0
92    0.525148        1                 1               1.0
93    0.531398        1                 1               1.0
94    0.517521        0                 0               1.0
95    0.539820        2                 2               1.0
96    0.531869        1                 1               1.0
97    0.527900        1                 1               1.0
98    0.539170        2                 2               1.0
99    0.527346        1                 1               1.0
100   0.531541        1                 1               1.0
101   0.543884        2                 2               1.0
102   0.540019        2                 2               1.0
103   0.523849        0                 0               1.0
104   0.531755        1                 1               1.0
105   0.524721        0                 0               1.0
106   0.550357        2                 2               1.0
107   0.533475        1                 1               1.0
108   0.515950        0                 0               1.0
109   0.559453        2                 2               1.0
110   0.538482        2                 2               1.0
111   0.521503        0                 0               1.0
112   0.523485        0                 0               1.0
113   0.524866        0                 0               1.0
114   0.523941        0                 0               1.0
115   0.531457        1                 1               1.0
116   0.533922        1                 1               1.0
117   0.532194        1                 1               1.0
118   0.531352        1                 1               1.0
119   0.560452        2                 2               1.0

In [48]:
T05_final_classification_model = finalize_model(T05_model_gbc)

In [49]:
T05_prediction = predict_model(T05_final_classification_model, data=T05_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [51]:
T05_y_class = pd.DataFrame(T05_class, columns = ['Y_Class'])
T05_idx = T05_y_class.index
T05_y_class = T05_y_class.reset_index()
T05_prediction = pd.concat([T05_prediction, T05_y_class], axis = 1)
T05_prediction = T05_prediction.set_index('index')
T05_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [52]:
T05_prediction

Y_Quality  prediction_label  prediction_score
index                                               
0       0.533277                 1            0.9980
1       0.541837                 2            0.9973
2       0.531457                 1            0.9980
3       0.537330                 2            0.9973
4       0.531651                 1            0.9980
...          ...               ...               ...
581     0.523485                 0            0.9972
582     0.522365                 0            0.9972
583     0.522453                 0            0.9972
594     0.523849                 0            0.9961
595     0.521306                 0            0.9972

[120 rows x 3 columns]

# T01

In [392]:
T01_class = T01['Y_Class']
T01_target = T01['Y_Quality']
T01_data = T01.drop(['Y_Class', 'Y_Quality'], axis = 1)
T01_data

PRODUCT_CODE  X_246  X_247  X_248  X_249  X_250  X_251  X_252  X_253  \
27              1    1.0   87.0  144.0   45.0   12.0    0.0   45.0   12.0   
28              1    1.0   89.0    0.0   45.0   11.0   90.0   45.0   11.0   
31              1    4.0   93.0  150.0   45.0   12.0    0.0   45.0   12.0   
32              1    1.0   89.0  152.0   45.0   12.0    0.0   45.0   12.0   
33              1    1.0   95.0    0.0   45.0   11.0   98.0   45.0   11.0   
..            ...    ...    ...    ...    ...    ...    ...    ...    ...   
531             1    1.0   90.0  142.0   45.0   11.0    0.0   45.0   12.0   
553             1    2.0   90.0    0.0   45.0   11.0  122.0   45.0   11.0   
554             1    1.0   89.0    0.0   45.0   11.0  122.0   45.0   11.0   
584             1    1.0   89.0    0.0   45.0   11.0   11.0   45.0   11.0   
585             1    1.0   93.0   63.0   45.0   12.0    0.0   45.0   12.0   

     X_254  ...  X_2856  X_2857      X_2858  X_2859  X_2860      X_2861  \
27    51.0  ...   177.1   186.2  169.907143   156.5   188.4  175.225000   
28    42.0  ...   170.5   186.8  182.758621   175.7   182.0  174.727586   
31    51.0  ...   170.8   207.8  191.775862   166.0   195.1  188.696552   
32    51.0  ...   174.5   190.7  181.686207   172.7   180.0  168.775862   
33    42.0  ...   173.2   195.0  184.365517   171.4   175.7  168.258621   
..     ...  ...     ...     ...         ...     ...     ...         ...   
531   51.0  ...   189.0   201.3  190.407143   181.1   192.6  185.207143   
553   42.0  ...   215.1   222.4  211.362069   195.7   201.2  191.286207   
554   42.0  ...   214.1   218.3  211.517857   205.1   193.9  185.071429   
584   42.0  ...   203.1   208.5  201.160714   193.0   207.1  195.682143   
585   51.0  ...   204.1   216.0  205.079310   196.1   192.2  187.396552   

     X_2862  X_2863      X_2864  X_2865  
27    159.9   446.0  430.442308   413.0  
28    160.5   446.0  429.716981   413.0  
31    181.7   446.0  429.245283   413.0  
32    154.1   446.0  429.981132   415.0  
33    158.3   446.0  429.301887   413.0  
..      ...     ...         ...     ...  
531   173.2   466.0  446.038461   427.0  
553   181.7   466.0  444.924528   424.0  
554   177.7   465.0  441.903846   423.0  
584   184.9   466.0  448.634615   432.0  
585   176.7   472.0  450.339623   432.0  

[129 rows x 895 columns]

In [58]:
T_01c = T01_data.columns
T_01scaler = StandardScaler()
T_01scaled = T_05scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
0             0.0 -0.383751 -1.444519  1.627125    0.0  1.343260 -0.736647   
1             0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
2             0.0  2.647096  0.739187  1.728952    0.0  1.343260 -0.736647   
3             0.0 -0.383751 -0.716617  1.762894    0.0  1.343260 -0.736647   
4             0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  1.167789   
..            ...       ...       ...       ...    ...       ...       ...   
124           0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
125           0.0  0.626531 -0.352666 -0.816720    0.0 -0.744457  1.634182   
126           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.634182   
127           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
128           0.0 -0.383751  0.739187  0.252462    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2856    X_2857    X_2858    X_2859  \
0      0.0  0.862116  0.918073  ... -0.460967 -0.947393 -1.614798 -1.613758   
1      0.0 -1.159937 -1.089239  ... -0.853081 -0.902251 -0.482382  0.021791   
2      0.0  0.862116  0.918073  ... -0.835258  0.677709  0.312177 -0.804502   
3      0.0  0.862116  0.918073  ... -0.615436 -0.608830 -0.576879 -0.233763   
4      0.0 -1.159937 -1.089239  ... -0.692671 -0.285314 -0.340790 -0.344503   
..     ...       ...       ...  ...       ...       ...       ...       ...   
124    0.0  0.862116  0.918073  ...  0.246027  0.188674  0.191572  0.481790   
125    0.0 -1.159937 -1.089239  ...  1.796661  1.776158  2.038027  1.725489   
126    0.0 -1.159937 -1.089239  ...  1.737250  1.467689  2.051754  2.526227   
127    0.0 -1.159937 -1.089239  ...  1.083726  0.730375  1.139129  1.495490   
128    0.0  0.862116  0.918073  ...  1.143137  1.294646  1.484418  1.759563   

       X_2860    X_2861    X_2862    X_2863    X_2864    X_2865  
0    0.587225  0.286139 -0.107506 -1.780047 -1.530483 -1.244903  
1   -0.057559  0.234620 -0.053298 -1.780047 -1.630148 -1.244903  
2    1.262234  1.681451  1.862054 -1.780047 -1.694963 -1.244903  
3   -0.259054 -0.381828 -0.631517 -1.780047 -1.593852 -0.977026  
4   -0.692268 -0.435401 -0.252061 -1.780047 -1.687185 -1.244903  
..        ...       ...       ...       ...       ...       ...  
124  1.010365  1.320037  1.094107  0.765696  0.612538  0.630239  
125  1.876793  1.949674  1.862054  0.765696  0.459476  0.228423  
126  1.141337  1.305980  1.500667  0.638409  0.044413  0.094484  
127  2.471204  2.404982  2.151164  0.765696  0.969268  1.299932  
128  0.970066  1.546804  1.410321  1.529419  1.203548  1.299932  

[129 rows x 895 columns]

In [59]:
T01_y_class = pd.DataFrame(T01_target, columns = ['Y_Quality'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_data = pd.concat([T01_data, T01_y_class], axis = 1)
T01_data = T01_data.set_index('index')
T01_data.drop(['Y_Quality'], axis = 1, inplace = True)
T01_data

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
index                                                                          
27              0.0 -0.383751 -1.444519  1.627125    0.0  1.343260 -0.736647   
28              0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
31              0.0  2.647096  0.739187  1.728952    0.0  1.343260 -0.736647   
32              0.0 -0.383751 -0.716617  1.762894    0.0  1.343260 -0.736647   
33              0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  1.167789   
...             ...       ...       ...       ...    ...       ...       ...   
531             0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
553             0.0  0.626531 -0.352666 -0.816720    0.0 -0.744457  1.634182   
554             0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.634182   
584             0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
585             0.0 -0.383751  0.739187  0.252462    0.0  1.343260 -0.736647   

       X_252     X_253     X_254  ...    X_2856    X_2857    X_2858    X_2859  \
index                             ...                                           
27       0.0  0.862116  0.918073  ... -0.460967 -0.947393 -1.614798 -1.613758   
28       0.0 -1.159937 -1.089239  ... -0.853081 -0.902251 -0.482382  0.021791   
31       0.0  0.862116  0.918073  ... -0.835258  0.677709  0.312177 -0.804502   
32       0.0  0.862116  0.918073  ... -0.615436 -0.608830 -0.576879 -0.233763   
33       0.0 -1.159937 -1.089239  ... -0.692671 -0.285314 -0.340790 -0.344503   
...      ...       ...       ...  ...       ...       ...       ...       ...   
531      0.0  0.862116  0.918073  ...  0.246027  0.188674  0.191572  0.481790   
553      0.0 -1.159937 -1.089239  ...  1.796661  1.776158  2.038027  1.725489   
554      0.0 -1.159937 -1.089239  ...  1.737250  1.467689  2.051754  2.526227   
584      0.0 -1.159937 -1.089239  ...  1.083726  0.730375  1.139129  1.495490   
585      0.0  0.862116  0.918073  ...  1.143137  1.294646  1.484418  1.759563   

         X_2860    X_2861    X_2862    X_2863    X_2864    X_2865  
index                                                              
27     0.587225  0.286139 -0.107506 -1.780047 -1.530483 -1.244903  
28    -0.057559  0.234620 -0.053298 -1.780047 -1.630148 -1.244903  
31     1.262234  1.681451  1.862054 -1.780047 -1.694963 -1.244903  
32    -0.259054 -0.381828 -0.631517 -1.780047 -1.593852 -0.977026  
33    -0.692268 -0.435401 -0.252061 -1.780047 -1.687185 -1.244903  
...         ...       ...       ...       ...       ...       ...  
531    1.010365  1.320037  1.094107  0.765696  0.612538  0.630239  
553    1.876793  1.949674  1.862054  0.765696  0.459476  0.228423  
554    1.141337  1.305980  1.500667  0.638409  0.044413  0.094484  
584    2.471204  2.404982  2.151164  0.765696  0.969268  1.299932  
585    0.970066  1.546804  1.410321  1.529419  1.203548  1.299932  

[129 rows x 895 columns]

In [61]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T01_data, target = T01_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [62]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbr = create_model('gbr', fold = 5)
T01_total_models.append(T01_model_gbr)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [63]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbr = tune_model(T01_model_gbr, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


In [64]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbr, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMRegressor(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
               importance_type='split', learning_rate=0.1, max_depth=-1,
               min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
               n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
               random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
               subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, c

In [65]:
for model in T01_tuned_models:
    display(predict_model(model))

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
90            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  2.139441   
91            0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  1.886811   
92            0.0  0.626531  0.011285  2.068375    0.0 -0.744457 -0.736647   
93            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.915160   
94            0.0 -0.383751 -1.080568  0.744625    0.0  1.343260 -0.736647   
95            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.309121   
96            0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
97            0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457 -0.192523   
98            0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.079540   
99            0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
100           0.0  0.626531 -0.716617  0.320347    0.0 -0.744457 -0.736647   
101           0.0 -0.383751  1.467090  1.525298    0.0  1.343260 -0.736647   
102           0.0 -0.383751 -1.080568 -0.816720    0.0 -0.744457  1.128923   
103           0.0  0.626531  0.011285 -0.816720    0.0 -0.744457  0.565365   
104           0.0 -0.383751  1.103139  1.576211    0.0  1.343260 -0.736647   
105           0.0 -0.383751 -0.352666 -0.816720    0.0 -0.744457 -0.056491   
106           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
107           0.0 -0.383751  0.739187 -0.748835    0.0 -0.744457 -0.736647   
108           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.770213   
109           0.0  0.626531 -1.080568  0.591885    0.0 -0.744457 -0.736647   
110           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
111           0.0 -0.383751  0.011285 -0.799749    0.0  1.343260 -0.736647   
112           0.0  0.626531 -1.080568 -0.816720    0.0 -0.744457  0.118406   
113           0.0  0.626531  1.831041  1.593183    0.0  1.343260 -0.736647   
114           0.0  0.626531  0.011285  0.557943    0.0  1.343260 -0.736647   
115           0.0 -0.383751  1.467090 -0.731864    0.0  1.343260 -0.736647   
116           0.0 -0.383751  1.831041  0.795539    0.0  1.343260 -0.736647   
117           0.0 -0.383751  1.103139  1.185875    0.0  1.343260 -0.736647   
118           0.0 -0.383751  1.831041 -0.782778    0.0  1.343260 -0.736647   
119           0.0 -0.383751  1.467090  0.303376    0.0 -0.744457 -0.736647   
120           0.0  0.626531 -0.716617 -0.816720    0.0 -0.744457  2.430936   
121           0.0 -0.383751 -0.716617  0.235491    0.0 -0.744457 -0.736647   
122           0.0  0.626531 -1.444519 -0.816720    0.0 -0.744457  1.711914   
123           0.0  9.719069 -0.352666 -0.816720    0.0 -0.744457  0.098973   
124           0.0  0.626531  0.739187  2.068375    0.0 -0.744457 -0.736647   
125           0.0 -0.383751 -0.352666  0.931308    0.0 -0.744457 -0.736647   
126           0.0 -0.383751  0.375236  1.762894    0.0 -0.744457 -0.736647   
127           0.0 -0.383751  0.739187 -0.477297    0.0  1.343260 -0.736647   
128           0.0 -0.383751  0.739187  0.439145    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2858    X_2859    X_2860    X_2861  \
90     0.0 -1.159937 -1.089239  ... -1.438284 -0.540429  1.645074  1.662522   
91     0.0 -1.159937 -1.089239  ... -1.682458 -0.966353 -2.193406 -1.655146   
92     0.0  0.862116  0.918073  ... -0.052320 -1.273019  1.161486  0.800314   
93     0.0 -1.159937 -1.089239  ...  0.311873  0.302902 -0.118007 -0.763269   
94     0.0  0.862116  0.918073  ...  0.751540  1.103639  0.577150  0.509271   
95     0.0 -1.159937 -1.089239  ... -0.618148 -1.221908  0.254758 -0.562063   
96     0.0 -1.159937 -1.089239  ...  0.186537  0.021791 -0.500848 -0.396344   
97     0.0 -1.159937 -1.089239  ... -0.172534 -0.889687 -0.793016 -0.621989   
98     0.0 -1.159937 -1.089239  ...  0.549069  0.839566 -0.954212 -1.035918   
99     0.0  0.862116  0.918073  ...  0.191572  0.481790  1.010365  1.320037   
100    0.0  0.8

In [66]:
T01_final_regression_model = finalize_model(T01_model_et)

In [67]:
T01_prediction = predict_model(T01_final_regression_model, data=T01_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [68]:
T01_datas = T01_prediction['prediction_label']

In [69]:
T01_datas = T01_prediction['prediction_label']
T01_datas = pd.DataFrame(T01_datas.values, columns = ['Y_Quality'])
T01_datas

Y_Quality
0     0.540002
1     0.521249
2     0.536206
3     0.548592
4     0.526656
..         ...
124   0.560317
125   0.524686
126   0.531106
127   0.519519
128   0.515214

[129 rows x 1 columns]

In [70]:
T01y_idx= T01_class.index
T01y_idx = pd.DataFrame(T01y_idx, columns = ['index'])
T01_datas = pd.concat([T01y_idx, T01_datas], axis = 1)
T01_datas = T01_datas.set_index('index')
T01_datas

Y_Quality
index           
27      0.540002
28      0.521249
31      0.536206
32      0.548592
33      0.526656
...          ...
531     0.560317
553     0.524686
554     0.531106
584     0.519519
585     0.515214

[129 rows x 1 columns]

In [71]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T01_datas, 
                   target=T01_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [72]:
T01_total_models = []

T01_model_lightgbm = create_model('lightgbm', fold = 5)
T01_total_models.append(T01_model_lightgbm)

T01_model_rf = create_model('rf', fold = 5)
T01_total_models.append(T01_model_rf)

T01_model_gbc = create_model('gbc', fold = 5)
T01_total_models.append(T01_model_gbc)

T01_model_et = create_model('et', fold = 5)
T01_total_models.append(T01_model_et)

T01_model_catboost = create_model('catboost', fold = 5)
T01_total_models.append(T01_model_catboost)

T01_model_xgb = create_model('xgboost', fold = 5)
T01_total_models.append(T01_model_xgb)

T01_model_ada = create_model('ada', fold = 5)
T01_total_models.append(T01_model_ada)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [73]:
T01_model_lightgbm = tune_model(T01_model_lightgbm, fold=5, choose_better = True)

T01_model_rf = tune_model(T01_model_rf, fold=5, choose_better = True)

T01_model_gbc = tune_model(T01_model_gbc, fold=5, choose_better = True)

T01_model_et = tune_model(T01_model_et, fold=5, choose_better = True)

T01_model_catboost = tune_model(T01_model_catboost, fold=5, choose_better = True)

T01_model_xgb = tune_model(T01_model_xgb, fold=5, choose_better = True)

T01_model_ada = tune_model(T01_model_ada, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [74]:
T01_tuned_models = [T01_model_lightgbm, T01_model_rf, T01_model_gbc, T01_model_et, T01_model_catboost, T01_model_xgb, T01_model_ada]
T01_tuned_models

[LGBMClassifier(boosting_type='gbdt', class_weight=None, colsample_bytree=1.0,
                importance_type='split', learning_rate=0.1, max_depth=-1,
                min_child_samples=20, min_child_weight=0.001, min_split_gain=0.0,
                n_estimators=100, n_jobs=-1, num_leaves=31, objective=None,
                random_state=414, reg_alpha=0.0, reg_lambda=0.0, silent=True,
                subsample=1.0, subsample_for_bin=200000, subsample_freq=0),
 RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight=None,
                        criterion='gini', max_depth=None, max_features='auto',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.0, min_samples_leaf=1,
                        min_samples_split=2, min_weight_fraction_leaf=0.0,
                        n_estimators=100, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp

In [75]:
for model in T01_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1            0.9992
91    0.523173        0                 0            0.9912
92    0.524408        0                 0            0.9912
93    0.523714        0                 0            0.9912
94    0.526460        1                 1            0.9940
95    0.519519        0                 0            0.9912
96    0.534716        1                 1            0.9958
97    0.560317        2                 2            0.9999
98    0.558770        2                 2            0.9999
99    0.547516        2                 2            0.9999
100   0.533944        1                 1            0.9992
101   0.538614        2                 2            0.9999
102   0.538806        2                 2            0.9999
103   0.529189        1                 1            0.9992
104   0.538030        2                 2            0.9999
105   0.533230        1                 1            0.9992
106   0.532890        1                 1            0.9992
107   0.529740        1                 1            0.9992
108   0.527910        1                 1            0.9992
109   0.524183        0                 0            0.9912
110   0.528270        1                 1            0.9992
111   0.537122        2                 2            0.9999
112   0.531036        1                 1            0.9992
113   0.527735        1                 1            0.9992
114   0.535589        2                 2            0.9999
115   0.544089        2                 2            0.9999
116   0.534403        1                 1            0.9992
117   0.531522        1                 1            0.9992
118   0.529171        1                 1            0.9992
119   0.533079        1                 1            0.9992
120   0.530514        1                 1            0.9992
121   0.530497        1                 1            0.9992
122   0.531583        1                 1            0.9992
123   0.527486        1                 1            0.9992
124   0.529070        1                 1            0.9992
125   0.533273        1                 1            0.9992
126   0.536859        2                 2            0.9999
127   0.513135        0                 0            0.9912
128   0.554498        2                 2            0.9999

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1              1.00
91    0.523173        0                 0              1.00
92    0.524408        0                 0              0.99
93    0.523714        0                 0              0.99
94    0.526460        1                 1              1.00
95    0.519519        0                 0              1.00
96    0.534716        1                 1              1.00
97    0.560317        2                 2              1.00
98    0.558770        2                 2              1.00
99    0.547516        2                 2              1.00
100   0.533944        1                 1              1.00
101   0.538614        2                 2              1.00
102   0.538806        2                 2              1.00
103   0.529189        1                 1              1.00
104   0.538030        2                 2              1.00
105   0.533230        1                 1              1.00
106   0.532890        1                 1              1.00
107   0.529740        1                 1              1.00
108   0.527910        1                 1              1.00
109   0.524183        0                 0              0.99
110   0.528270        1                 1              1.00
111   0.537122        2                 2              1.00
112   0.531036        1                 1              1.00
113   0.527735        1                 1              1.00
114   0.535589        2                 2              1.00
115   0.544089        2                 2              1.00
116   0.534403        1                 1              1.00
117   0.531522        1                 1              1.00
118   0.529171        1                 1              1.00
119   0.533079        1                 1              1.00
120   0.530514        1                 1              1.00
121   0.530497        1                 1              1.00
122   0.531583        1                 1              1.00
123   0.527486        1                 1              1.00
124   0.529070        1                 1              1.00
125   0.533273        1                 1              1.00
126   0.536859        2                 2              1.00
127   0.513135        0                 0              1.00
128   0.554498        2                 2              1.00

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1               1.0
91    0.523173        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523714        0                 0               1.0
94    0.526460        1                 1               1.0
95    0.519519        0                 0               1.0
96    0.534716        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.558770        2                 2               1.0
99    0.547516        2                 2               1.0
100   0.533944        1                 1               1.0
101   0.538614        2                 2               1.0
102   0.538806        2                 2               1.0
103   0.529189        1                 1               1.0
104   0.538030        2                 2               1.0
105   0.533230        1                 1               1.0
106   0.532890        1                 1               1.0
107   0.529740        1                 1               1.0
108   0.527910        1                 1               1.0
109   0.524183        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.537122        2                 2               1.0
112   0.531036        1                 1               1.0
113   0.527735        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.544089        2                 2               1.0
116   0.534403        1                 1               1.0
117   0.531522        1                 1               1.0
118   0.529171        1                 1               1.0
119   0.533079        1                 1               1.0
120   0.530514        1                 1               1.0
121   0.530497        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.527486        1                 1               1.0
124   0.529070        1                 1               1.0
125   0.533273        1                 1               1.0
126   0.536859        2                 2               1.0
127   0.513135        0                 0               1.0
128   0.554498        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1               1.0
91    0.523173        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523714        0                 0               1.0
94    0.526460        1                 1               1.0
95    0.519519        0                 0               1.0
96    0.534716        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.558770        2                 2               1.0
99    0.547516        2                 2               1.0
100   0.533944        1                 1               1.0
101   0.538614        2                 2               1.0
102   0.538806        2                 2               1.0
103   0.529189        1                 1               1.0
104   0.538030        2                 2               1.0
105   0.533230        1                 1               1.0
106   0.532890        1                 1               1.0
107   0.529740        1                 1               1.0
108   0.527910        1                 1               1.0
109   0.524183        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.537122        2                 2               1.0
112   0.531036        1                 1               1.0
113   0.527735        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.544089        2                 2               1.0
116   0.534403        1                 1               1.0
117   0.531522        1                 1               1.0
118   0.529171        1                 1               1.0
119   0.533079        1                 1               1.0
120   0.530514        1                 1               1.0
121   0.530497        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.527486        1                 1               1.0
124   0.529070        1                 1               1.0
125   0.533273        1                 1               1.0
126   0.536859        2                 2               1.0
127   0.513135        0                 0               1.0
128   0.554498        2                 2               1.0

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1            0.9996
91    0.523173        0                 0            0.9975
92    0.524408        0                 0            0.9969
93    0.523714        0                 0            0.9975
94    0.526460        1                 1            0.9990
95    0.519519        0                 0            0.9977
96    0.534716        1                 1            0.9813
97    0.560317        2                 2            0.9980
98    0.558770        2                 2            0.9980
99    0.547516        2                 2            0.9989
100   0.533944        1                 1            0.9994
101   0.538614        2                 2            0.9991
102   0.538806        2                 2            0.9991
103   0.529189        1                 1            0.9995
104   0.538030        2                 2            0.9990
105   0.533230        1                 1            0.9995
106   0.532890        1                 1            0.9995
107   0.529740        1                 1            0.9995
108   0.527910        1                 1            0.9994
109   0.524183        0                 0            0.9969
110   0.528270        1                 1            0.9994
111   0.537122        2                 2            0.9990
112   0.531036        1                 1            0.9995
113   0.527735        1                 1            0.9993
114   0.535589        2                 2            0.9970
115   0.544089        2                 2            0.9991
116   0.534403        1                 1            0.9991
117   0.531522        1                 1            0.9995
118   0.529171        1                 1            0.9995
119   0.533079        1                 1            0.9995
120   0.530514        1                 1            0.9996
121   0.530497        1                 1            0.9996
122   0.531583        1                 1            0.9995
123   0.527486        1                 1            0.9993
124   0.529070        1                 1            0.9995
125   0.533273        1                 1            0.9995
126   0.536859        2                 2            0.9989
127   0.513135        0                 0            0.9973
128   0.554498        2                 2            0.9986

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1            0.9953
91    0.523173        0                 0            0.9665
92    0.524408        0                 0            0.9665
93    0.523714        0                 0            0.9665
94    0.526460        1                 1            0.9799
95    0.519519        0                 0            0.9665
96    0.534716        1                 1            0.9813
97    0.560317        2                 2            0.9836
98    0.558770        2                 2            0.9836
99    0.547516        2                 2            0.9836
100   0.533944        1                 1            0.9859
101   0.538614        2                 2            0.9836
102   0.538806        2                 2            0.9836
103   0.529189        1                 1            0.9953
104   0.538030        2                 2            0.9836
105   0.533230        1                 1            0.9872
106   0.532890        1                 1            0.9879
107   0.529740        1                 1            0.9953
108   0.527910        1                 1            0.9953
109   0.524183        0                 0            0.9665
110   0.528270        1                 1            0.9953
111   0.537122        2                 2            0.9836
112   0.531036        1                 1            0.9953
113   0.527735        1                 1            0.9949
114   0.535589        2                 2            0.9836
115   0.544089        2                 2            0.9836
116   0.534403        1                 1            0.9840
117   0.531522        1                 1            0.9953
118   0.529171        1                 1            0.9953
119   0.533079        1                 1            0.9879
120   0.530514        1                 1            0.9953
121   0.530497        1                 1            0.9953
122   0.531583        1                 1            0.9953
123   0.527486        1                 1            0.9949
124   0.529070        1                 1            0.9953
125   0.533273        1                 1            0.9872
126   0.536859        2                 2            0.9836
127   0.513135        0                 0            0.9665
128   0.554498        2                 2            0.9836

Y_Quality  Y_Class  prediction_label  prediction_score
90    0.530625        1                 1               1.0
91    0.523173        0                 0               1.0
92    0.524408        0                 0               1.0
93    0.523714        0                 0               1.0
94    0.526460        1                 1               1.0
95    0.519519        0                 0               1.0
96    0.534716        1                 1               1.0
97    0.560317        2                 2               1.0
98    0.558770        2                 2               1.0
99    0.547516        2                 2               1.0
100   0.533944        1                 1               1.0
101   0.538614        2                 2               1.0
102   0.538806        2                 2               1.0
103   0.529189        1                 1               1.0
104   0.538030        2                 2               1.0
105   0.533230        1                 1               1.0
106   0.532890        1                 1               1.0
107   0.529740        1                 1               1.0
108   0.527910        1                 1               1.0
109   0.524183        0                 0               1.0
110   0.528270        1                 1               1.0
111   0.537122        2                 2               1.0
112   0.531036        1                 1               1.0
113   0.527735        1                 1               1.0
114   0.535589        2                 2               1.0
115   0.544089        2                 2               1.0
116   0.534403        1                 1               1.0
117   0.531522        1                 1               1.0
118   0.529171        1                 1               1.0
119   0.533079        1                 1               1.0
120   0.530514        1                 1               1.0
121   0.530497        1                 1               1.0
122   0.531583        1                 1               1.0
123   0.527486        1                 1               1.0
124   0.529070        1                 1               1.0
125   0.533273        1                 1               1.0
126   0.536859        2                 2               1.0
127   0.513135        0                 0               1.0
128   0.554498        2                 2               1.0

In [76]:
T01_final_classification_model = finalize_model(T01_model_xgb)

In [78]:
T01_prediction = predict_model(T01_final_classification_model, data=T01_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [79]:
T01_y_class = pd.DataFrame(T01_class, columns = ['Y_Class'])
T01_idx = T01_y_class.index
T01_y_class = T01_y_class.reset_index()
T01_prediction = pd.concat([T01_prediction, T01_y_class], axis = 1)
T01_prediction = T01_prediction.set_index('index')
T01_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [80]:
T01_prediction

Y_Quality  prediction_label  prediction_score
index                                               
27      0.540002                 2            0.9885
28      0.521249                 0            0.9776
31      0.536206                 2            0.9885
32      0.548592                 2            0.9885
33      0.526656                 1            0.9835
...          ...               ...               ...
531     0.560317                 2            0.9885
553     0.524686                 0            0.9776
554     0.531106                 1            0.9967
584     0.519519                 0            0.9776
585     0.515214                 0            0.9776

[129 rows x 3 columns]

# T10

In [393]:
T10_class = T10['Y_Class']
T10_target = T10['Y_Quality']
T10_data = T10.drop(['Y_Class', 'Y_Quality'], axis = 1)
T10_data

PRODUCT_CODE   X_1    X_2  X_3   X_4   X_5  X_6   X_7   X_8   X_9  ...  \
22              2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
23              2   2.0  102.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
25              2   2.0   97.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
26              2   2.0   95.0  0.0  45.0  10.0  0.0  54.0  10.0  52.0  ...   
29              2   2.0  100.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
..            ...   ...    ...  ...   ...   ...  ...   ...   ...   ...  ...   
591             2   1.0   87.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
592             2   2.0   98.0  0.0  45.0  10.0  0.0  45.0  10.0  31.0  ...   
593             2   2.0   95.0  0.0  45.0  10.0  0.0  50.0  10.0  52.0  ...   
596             3  40.0   94.0  0.0  45.0  11.0  0.0  45.0  10.0  31.0  ...   
597             3  21.0   87.0  0.0  45.0  10.0  0.0  61.0  10.0  52.0  ...   

     X_924  X_925       X_926  X_927  X_928       X_929  X_930  X_931  \
22   172.5  162.8  157.235484  150.9  326.0  309.290909  290.0   13.7   
23     0.0    0.0    0.000000    0.0    0.0    0.000000    0.0    0.0   
25   177.8  157.1  154.074194  150.9  327.0  310.854546  298.0   13.7   
26   166.9  158.5  151.096774  146.5  327.0  313.618182  299.0   13.7   
29   177.9  161.3  156.038710  149.1  327.0  312.109091  298.0   13.7   
..     ...    ...         ...    ...    ...         ...    ...    ...   
591  177.0  159.6  154.777419  147.7  326.0  313.472727  298.0   13.6   
592  171.5  156.6  152.535484  147.6  326.0  312.472727  298.0   13.6   
593  172.8  161.2  155.438710  149.0  327.0  313.363636  298.0   13.6   
596  189.2  179.5  173.190323  168.6  321.0  303.036364  289.0   13.6   
597  188.2  172.9  167.087097  161.1  326.0  304.818182  289.0   13.6   

         X_932  X_933  
22   13.443333   13.2  
23    0.000000    0.0  
25   13.454839   13.2  
26   13.461290   13.3  
29   13.422581   13.2  
..         ...    ...  
591  13.400000   13.2  
592  13.361290   13.2  
593  13.351613   13.2  
596  13.406667   13.2  
597  13.380000   13.2  

[349 rows x 678 columns]

In [82]:
T_10c = T10_data.columns
T_10scaler = StandardScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
0       -0.132260 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
1       -0.132260 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
2       -0.132260 -0.069603  0.457558  0.0  0.0  1.243964  0.0 -0.870577   
3       -0.132260 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  1.190073   
4       -0.132260 -0.069603  1.188953  0.0  0.0  1.243964  0.0 -0.870577   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344     -0.132260 -0.239475 -1.980425  0.0  0.0 -0.803882  0.0  0.274229   
345     -0.132260 -0.069603  0.701357  0.0  0.0 -0.803882  0.0 -0.870577   
346     -0.132260 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  0.274229   
347      7.560864  6.385512 -0.273837  0.0  0.0  1.243964  0.0 -0.870577   
348      7.560864  3.157954 -1.980425  0.0  0.0 -0.803882  0.0  2.792801   

          X_8       X_9  ...      X_924      X_925      X_926      X_927  \
0   -0.226285 -0.997139  ...  -0.005131   0.278454   0.389930   0.438042   
1   -0.226285 -0.997139  ... -16.700869 -17.224533 -17.459659 -16.729021   
2   -0.226285 -0.997139  ...   0.507840  -0.334366   0.031056   0.438042   
3   -0.226285  1.002869  ...  -0.547137  -0.183849  -0.306945  -0.062522   
4   -0.226285 -0.997139  ...   0.517519   0.117185   0.254071   0.233266   
..        ...       ...  ...        ...        ...        ...        ...   
344 -0.226285  1.002869  ...   0.430410  -0.065586   0.110887   0.073996   
345 -0.226285 -0.997139  ...  -0.101917  -0.388122  -0.143620   0.062619   
346 -0.226285  1.002869  ...   0.023906   0.106434   0.185958   0.221890   
347 -0.226285 -0.997139  ...   1.611211   2.073907   2.201145   2.451674   
348 -0.226285  1.002869  ...   1.514424   1.364327   1.508299   1.598440   

         X_928      X_929      X_930      X_931      X_932      X_933  
0     0.207541   0.177997  -0.040715   0.134006   0.100241   0.036419  
1   -18.026231 -18.033575 -17.957129 -18.600584 -18.606323 -18.605157  
2     0.263473   0.270066   0.453531   0.134006   0.116251   0.036419  
3     0.263473   0.432794   0.515312   0.134006   0.125228   0.177643  
4     0.263473   0.343936   0.453531   0.134006   0.071363   0.036419  
..         ...        ...        ...        ...        ...        ...  
344   0.207541   0.424229   0.453531  -0.002743   0.039942   0.036419  
345   0.207541   0.365347   0.453531  -0.002743  -0.013923   0.036419  
346   0.263473   0.417806   0.453531  -0.002743  -0.027389   0.036419  
347  -0.072118  -0.190282  -0.102496  -0.002743   0.049219   0.036419  
348   0.207541  -0.085365  -0.102496  -0.002743   0.012112   0.036419  

[349 rows x 678 columns]

In [83]:
T10_y_class = pd.DataFrame(T10_target, columns = ['Y_Quality'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_data = pd.concat([T10_data, T10_y_class], axis = 1)
T10_data = T10_data.set_index('index')
T10_data.drop(['Y_Quality'], axis = 1, inplace = True)
T10_data

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
index                                                                        
22        -0.132260 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
23        -0.132260 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
25        -0.132260 -0.069603  0.457558  0.0  0.0  1.243964  0.0 -0.870577   
26        -0.132260 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  1.190073   
29        -0.132260 -0.069603  1.188953  0.0  0.0  1.243964  0.0 -0.870577   
...             ...       ...       ...  ...  ...       ...  ...       ...   
591       -0.132260 -0.239475 -1.980425  0.0  0.0 -0.803882  0.0  0.274229   
592       -0.132260 -0.069603  0.701357  0.0  0.0 -0.803882  0.0 -0.870577   
593       -0.132260 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  0.274229   
596        7.560864  6.385512 -0.273837  0.0  0.0  1.243964  0.0 -0.870577   
597        7.560864  3.157954 -1.980425  0.0  0.0 -0.803882  0.0  2.792801   

            X_8       X_9  ...      X_924      X_925      X_926      X_927  \
index                      ...                                               
22    -0.226285 -0.997139  ...  -0.005131   0.278454   0.389930   0.438042   
23    -0.226285 -0.997139  ... -16.700869 -17.224533 -17.459659 -16.729021   
25    -0.226285 -0.997139  ...   0.507840  -0.334366   0.031056   0.438042   
26    -0.226285  1.002869  ...  -0.547137  -0.183849  -0.306945  -0.062522   
29    -0.226285 -0.997139  ...   0.517519   0.117185   0.254071   0.233266   
...         ...       ...  ...        ...        ...        ...        ...   
591   -0.226285  1.002869  ...   0.430410  -0.065586   0.110887   0.073996   
592   -0.226285 -0.997139  ...  -0.101917  -0.388122  -0.143620   0.062619   
593   -0.226285  1.002869  ...   0.023906   0.106434   0.185958   0.221890   
596   -0.226285 -0.997139  ...   1.611211   2.073907   2.201145   2.451674   
597   -0.226285  1.002869  ...   1.514424   1.364327   1.508299   1.598440   

           X_928      X_929      X_930      X_931      X_932      X_933  
index                                                                    
22      0.207541   0.177997  -0.040715   0.134006   0.100241   0.036419  
23    -18.026231 -18.033575 -17.957129 -18.600584 -18.606323 -18.605157  
25      0.263473   0.270066   0.453531   0.134006   0.116251   0.036419  
26      0.263473   0.432794   0.515312   0.134006   0.125228   0.177643  
29      0.263473   0.343936   0.453531   0.134006   0.071363   0.036419  
...          ...        ...        ...        ...        ...        ...  
591     0.207541   0.424229   0.453531  -0.002743   0.039942   0.036419  
592     0.207541   0.365347   0.453531  -0.002743  -0.013923   0.036419  
593     0.263473   0.417806   0.453531  -0.002743  -0.027389   0.036419  
596    -0.072118  -0.190282  -0.102496  -0.002743   0.049219   0.036419  
597     0.207541  -0.085365  -0.102496  -0.002743   0.012112   0.036419  

[349 rows x 678 columns]

In [85]:
#13
from pycaret.regression import *
setup_rgs = setup(data = T10_data, target = T10_target, session_id = 414)
top5 = compare_models(sort='MSE', n_select=5)

Processing:   0%|          | 0/89 [00:00<?, ?it/s]

In [86]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbr = create_model('gbr', fold = 5)
T10_total_models.append(T10_model_gbr)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [87]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbr = tune_model(T10_model_gbr, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [88]:
T10_tuned_models = [T10_model_rf, T10_model_gbr, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestRegressor(bootstrap=True, ccp_alpha=0.0, criterion='squared_error',
                       max_depth=None, max_features='auto', max_leaf_nodes=None,
                       max_samples=None, min_impurity_decrease=0.0,
                       min_samples_leaf=1, min_samples_split=2,
                       min_weight_fraction_leaf=0.0, n_estimators=100, n_jobs=-1,
                       oob_score=False, random_state=414, verbose=0,
                       warm_start=False),
 GradientBoostingRegressor(alpha=0.9, ccp_alpha=0.0, criterion='friedman_mse',
                           init=None, learning_rate=0.1, loss='squared_error',
                           max_depth=3, max_features=None, max_leaf_nodes=None,
                           min_impurity_decrease=0.0, min_samples_leaf=1,
                           min_samples_split=2, min_weight_fraction_leaf=0.0,
                           n_estimators=100, n_iter_no_change=None,
                           random_state=414, subsample=

In [89]:
for model in T10_tuned_models:
    display(predict_model(model))

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.529992  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.530912  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.530941  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.529405  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.530522  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.531202  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.529938  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.529585  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.529877  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.530451  

[105 rows x 680 columns]

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.528352  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.531208  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.530546  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.531667  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.530300  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.534161  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.531506  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.528019  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.529378  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.529680  

[105 rows x 680 columns]

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.528858  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.529889  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.530017  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.531080  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.530354  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.532355  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.530558  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.528888  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.529350  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.530358  

[105 rows x 680 columns]

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.528144  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.530474  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.531365  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.530336  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.529309  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.533729  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.530094  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.528618  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.530465  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.529611  

[105 rows x 680 columns]

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.529982  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.529315  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.533774  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.530048  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.529679  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.534121  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.531274  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.531469  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.530026  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.529908  

[105 rows x 680 columns]

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.530269  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.530233  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.530302  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.530259  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.530288  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.530322  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.530269  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.530233  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.530259  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.530259  

[105 rows x 680 columns]

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
244      -0.13226 -0.069603  0.213760  0.0  0.0  1.243963  0.0 -0.870577   
245      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
246      -0.13226 -0.069603  0.701357  0.0  0.0  1.243963  0.0 -0.870577   
247      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
248      -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
345      -0.13226 -0.069603  1.676550  0.0  0.0  1.243963  0.0 -0.870577   
346      -0.13226 -0.069603  1.432752  0.0  0.0  1.243963  0.0 -0.870577   
347      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0 -0.870577   
348      -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_926     X_927     X_928     X_929  \
244 -0.226285 -0.997139  ...  0.330240  0.415289 -0.295846 -0.143176   
245 -0.226285 -0.997139  ... -0.016184  0.119502  0.263472  0.433864   
246 -0.226285 -0.997139  ...  0.067310  0.051243  0.207541 -0.107847   
247 -0.226285 -0.997139  ...  0.050465  0.119502  0.207541  0.249725   
248 -0.226285  1.002869  ... -0.120550 -0.039769  0.151609 -0.074659   
..        ...       ...  ...       ...       ...       ...       ...   
344 -0.226285 -0.997139  ... -0.298888  0.005737  0.207541  0.120185   
345 -0.226285 -0.997139  ... -0.612720 -0.335556  0.263472  0.241161   
346 -0.226285 -0.997139  ... -0.066670  0.233266  0.263472  0.123794   
347 -0.226285 -0.997139  ... -0.562917 -0.426568 -0.295846 -0.305904   
348 -0.226285  1.002869  ... -0.013254 -0.039769  0.151609 -0.102494   

        X_930     X_931     X_932     X_933  Y_Quality  prediction_label  
244 -0.164277  0.134006  0.053408  0.036419   0.529167          0.526818  
245  0.453531 -0.002743  0.030965  0.036419   0.532317          0.533790  
246 -0.102496 -0.002743  0.049219  0.036419   0.526232          0.529182  
247 -0.102496 -0.002743 -0.063299 -0.104805   0.532694          0.532181  
248 -0.040715 -0.139492 -0.085294 -0.104805   0.527637          0.530275  
..        ...       ...       ...       ...        ...               ...  
344 -0.102496 -0.002743 -0.063299  0.036419   0.528154          0.531719  
345  0.453531 -0.002743  0.035453  0.036419   0.529000          0.531448  
346 -0.102496  0.134006  0.138695  0.177643   0.529097          0.529107  
347 -0.349619 -0.002743 -0.006442 -0.104805   0.532446          0.531902  
348 -0.102496 -0.002743  0.013010  0.036419   0.532122          0.530110  

[105 rows x 680 columns]

In [90]:
T10_final_regression_model = finalize_model(T10_model_lightgbm)

In [91]:
T10_prediction = predict_model(T10_final_regression_model, data=T10_data)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [92]:
T10_datas = T10_prediction['prediction_label']

In [93]:
T10_datas = T10_prediction['prediction_label']
T10_datas = pd.DataFrame(T10_datas.values, columns = ['Y_Quality'])
T10_datas

Y_Quality
0     0.517982
1     0.519350
2     0.529565
3     0.531354
4     0.532115
..         ...
344   0.528472
345   0.528400
346   0.526965
347   0.531267
348   0.531900

[349 rows x 1 columns]

In [94]:
T10y_idx= T10_class.index
T10y_idx = pd.DataFrame(T10y_idx, columns = ['index'])
T10_datas = pd.concat([T10y_idx, T10_datas], axis = 1)
T10_datas = T10_datas.set_index('index')
T10_datas

Y_Quality
index           
22      0.517982
23      0.519350
25      0.529565
26      0.531354
29      0.532115
...          ...
591     0.528472
592     0.528400
593     0.526965
596     0.531267
597     0.531900

[349 rows x 1 columns]

In [95]:
from pycaret.classification import *
# 분류 패키지의 모든 모듈을 임포트한다.
exp_clf101 = setup(data=T10_datas, 
                   target=T10_class, 
                   fold=5,
                   session_id=414)
top5 = compare_models(sort='Accuracy', n_select=5)

Processing:   0%|          | 0/73 [00:00<?, ?it/s]

In [96]:
T10_total_models = []

T10_model_rf = create_model('rf', fold = 5)
T10_total_models.append(T10_model_rf)

T10_model_gbc = create_model('gbc', fold = 5)
T10_total_models.append(T10_model_gbc)

T10_model_et = create_model('et', fold = 5)
T10_total_models.append(T10_model_et)

T10_model_catboost = create_model('catboost', fold = 5)
T10_total_models.append(T10_model_catboost)

T10_model_xgb = create_model('xgboost', fold = 5)
T10_total_models.append(T10_model_xgb)

T10_model_ada = create_model('ada', fold = 5)
T10_total_models.append(T10_model_ada)

T10_model_lightgbm = create_model('lightgbm', fold = 5)
T10_total_models.append(T10_model_lightgbm)

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

Processing:   0%|          | 0/4 [00:00<?, ?it/s]

In [97]:
T10_model_rf = tune_model(T10_model_rf, fold=5, choose_better = True)

T10_model_gbc = tune_model(T10_model_gbc, fold=5, choose_better = True)

T10_model_et = tune_model(T10_model_et, fold=5, choose_better = True)

T10_model_catboost = tune_model(T10_model_catboost, fold=5, choose_better = True)

T10_model_xgb = tune_model(T10_model_xgb, fold=5, choose_better = True)

T10_model_ada = tune_model(T10_model_ada, fold=5, choose_better = True)

T10_model_lightgbm = tune_model(T10_model_lightgbm, fold=5, choose_better = True)

Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

...

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits


Processing:   0%|          | 0/7 [00:00<?, ?it/s]

Fitting 5 folds for each of 10 candidates, totalling 50 fits
Original model was better than the tuned model, hence it will be returned. NOTE: The display metrics are for the tuned model (not the original one).


In [98]:
T10_tuned_models = [T10_model_rf, T10_model_gbc, T10_model_et, T10_model_catboost, T10_model_xgb, T10_model_ada, T10_model_lightgbm]
T10_tuned_models

[RandomForestClassifier(bootstrap=True, ccp_alpha=0.0, class_weight={},
                        criterion='entropy', max_depth=5, max_features='sqrt',
                        max_leaf_nodes=None, max_samples=None,
                        min_impurity_decrease=0.3, min_samples_leaf=3,
                        min_samples_split=10, min_weight_fraction_leaf=0.0,
                        n_estimators=170, n_jobs=-1, oob_score=False,
                        random_state=414, verbose=0, warm_start=False),
 GradientBoostingClassifier(ccp_alpha=0.0, criterion='friedman_mse', init=None,
                            learning_rate=0.01, loss='deviance', max_depth=7,
                            max_features=1.0, max_leaf_nodes=None,
                            min_impurity_decrease=0.1, min_samples_leaf=2,
                            min_samples_split=10, min_weight_fraction_leaf=0.0,
                            n_estimators=270, n_iter_no_change=None,
                            random_state=414, su

In [99]:
for model in T10_tuned_models:
    display(predict_model(model))

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1            0.9659
245   0.531267        1                 1            0.9659
246   0.529617        1                 1            0.9659
247   0.529050        1                 1            0.9659
248   0.519350        0                 0            0.9611
..         ...      ...               ...               ...
344   0.527032        1                 1            0.9659
345   0.528400        1                 1            0.9659
346   0.524781        0                 0            0.9611
347   0.533633        1                 1            0.9659
348   0.533293        1                 1            0.9659

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1            0.9867
245   0.531267        1                 1            0.9867
246   0.529617        1                 1            0.9867
247   0.529050        1                 1            0.9867
248   0.519350        0                 0            0.9353
..         ...      ...               ...               ...
344   0.527032        1                 1            0.9867
345   0.528400        1                 1            0.9867
346   0.524781        0                 0            0.9353
347   0.533633        1                 1            0.9515
348   0.533293        1                 1            0.9285

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1               1.0
245   0.531267        1                 1               1.0
246   0.529617        1                 1               1.0
247   0.529050        1                 1               1.0
248   0.519350        0                 0               1.0
..         ...      ...               ...               ...
344   0.527032        1                 1               1.0
345   0.528400        1                 1               1.0
346   0.524781        0                 0               1.0
347   0.533633        1                 1               1.0
348   0.533293        1                 1               1.0

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1            0.8948
245   0.531267        1                 1            0.8984
246   0.529617        1                 1            0.8960
247   0.529050        1                 1            0.8929
248   0.519350        0                 0            0.7787
..         ...      ...               ...               ...
344   0.527032        1                 1            0.8701
345   0.528400        1                 1            0.8978
346   0.524781        0                 0            0.7787
347   0.533633        1                 1            0.7750
348   0.533293        1                 1            0.7974

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1            0.5129
245   0.531267        1                 1            0.5165
246   0.529617        1                 1            0.5165
247   0.529050        1                 1            0.5165
248   0.519350        0                 0            0.5014
..         ...      ...               ...               ...
344   0.527032        1                 1            0.5165
345   0.528400        1                 1            0.5165
346   0.524781        0                 0            0.4834
347   0.533633        1                 1            0.4856
348   0.533293        1                 1            0.4925

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1            0.4169
245   0.531267        1                 1            0.4169
246   0.529617        1                 1            0.4169
247   0.529050        1                 1            0.4169
248   0.519350        0                 0            0.3836
..         ...      ...               ...               ...
344   0.527032        1                 1            0.4169
345   0.528400        1                 1            0.4169
346   0.524781        0                 0            0.3836
347   0.533633        1                 1            0.3813
348   0.533293        1                 1            0.3813

[105 rows x 4 columns]

Y_Quality  Y_Class  prediction_label  prediction_score
244   0.532867        1                 1            0.9997
245   0.531267        1                 1            0.9997
246   0.529617        1                 1            0.9997
247   0.529050        1                 1            0.9997
248   0.519350        0                 0            0.9983
..         ...      ...               ...               ...
344   0.527032        1                 1            0.9996
345   0.528400        1                 1            0.9997
346   0.524781        0                 0            0.9983
347   0.533633        1                 1            0.9915
348   0.533293        1                 1            0.6891

[105 rows x 4 columns]

In [100]:
T10_final_classification_model = finalize_model(T10_model_xgb)

In [101]:
T10_prediction = predict_model(T10_final_classification_model, data=T10_datas)
#prediction.drop(['Y_Quality'], axis = 1, inplace = True)

In [102]:
T10_y_class = pd.DataFrame(T10_class, columns = ['Y_Class'])
T10_idx = T10_y_class.index
T10_y_class = T10_y_class.reset_index()
T10_prediction = pd.concat([T10_prediction, T10_y_class], axis = 1)
T10_prediction = T10_prediction.set_index('index')
T10_prediction.drop(['Y_Class'], axis = 1, inplace = True)

In [103]:
T10_prediction

Y_Quality  prediction_label  prediction_score
index                                               
22      0.517982                 0            0.5107
23      0.519350                 0            0.5107
25      0.529565                 1            0.5164
26      0.531354                 1            0.5164
29      0.532115                 1            0.5164
...          ...               ...               ...
591     0.528472                 1            0.5164
592     0.528400                 1            0.5164
593     0.526965                 1            0.5164
596     0.531267                 1            0.5164
597     0.531900                 1            0.5164

[349 rows x 3 columns]

# Test

In [394]:
#44
test_data = pd.read_csv("./test.csv")
test_data

PRODUCT_ID         TIMESTAMP     LINE PRODUCT_CODE  X_1   X_2  X_3   X_4  \
0     TEST_000   2022-09-09 2:01  T100306         T_31  2.0  94.0  0.0  45.0   
1     TEST_001   2022-09-09 2:09  T100304         T_31  2.0  93.0  0.0  45.0   
2     TEST_002   2022-09-09 8:42  T100304         T_31  2.0  95.0  0.0  45.0   
3     TEST_003  2022-09-09 10:56  T010305         A_31  NaN   NaN  NaN   NaN   
4     TEST_004  2022-09-09 11:04  T010306         A_31  NaN   NaN  NaN   NaN   
..         ...               ...      ...          ...  ...   ...  ...   ...   
305   TEST_305  2022-11-05 11:18  T100306         T_31  2.0  91.0  0.0  45.0   
306   TEST_306  2022-11-05 16:39  T100304         T_31  2.0  96.0  0.0  45.0   
307   TEST_307  2022-11-05 16:47  T100306         T_31  2.0  91.0  0.0  45.0   
308   TEST_308  2022-11-05 20:53  T100306         T_31  2.0  95.0  0.0  45.0   
309   TEST_309  2022-11-05 21:01  T100306         T_31  2.0  87.0  0.0  45.0   

      X_5  X_6  ...  X_2866  X_2867  X_2868  X_2869  X_2870  X_2871  X_2872  \
0    10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
1    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
2    11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
3     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
4     NaN  NaN  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
..    ...  ...  ...     ...     ...     ...     ...     ...     ...     ...   
305  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
306  11.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
307  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
308  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   
309  10.0  0.0  ...     NaN     NaN     NaN     NaN     NaN     NaN     NaN   

     X_2873  X_2874  X_2875  
0       NaN     NaN     NaN  
1       NaN     NaN     NaN  
2       NaN     NaN     NaN  
3       NaN     NaN     NaN  
4       NaN     NaN     NaN  
..      ...     ...     ...  
305     NaN     NaN     NaN  
306     NaN     NaN     NaN  
307     NaN     NaN     NaN  
308     NaN     NaN     NaN  
309     NaN     NaN     NaN  

[310 rows x 2879 columns]

In [395]:
test_data.drop(colls, inplace = True, axis = 1)

In [396]:
test_data.loc[test_data.PRODUCT_CODE == 'A_31','PRODUCT_CODE'] = 1
test_data.loc[test_data.PRODUCT_CODE == 'T_31','PRODUCT_CODE'] = 2
test_data.loc[test_data.PRODUCT_CODE == 'O_31','PRODUCT_CODE'] = 3

test_data.drop(['PRODUCT_ID', 'TIMESTAMP'], axis = 1, inplace = True)
test_data

LINE PRODUCT_CODE  X_1   X_2  X_3   X_4   X_5  X_6   X_7   X_8  ...  \
0    T100306            2  2.0  94.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
1    T100304            2  2.0  93.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
2    T100304            2  2.0  95.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
3    T010305            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
4    T010306            1  NaN   NaN  NaN   NaN   NaN  NaN   NaN   NaN  ...   
..       ...          ...  ...   ...  ...   ...   ...  ...   ...   ...  ...   
305  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
306  T100304            2  2.0  96.0  0.0  45.0  11.0  0.0  45.0  10.0  ...   
307  T100306            2  2.0  91.0  0.0  45.0  10.0  0.0  50.0  10.0  ...   
308  T100306            2  2.0  95.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   
309  T100306            2  2.0  87.0  0.0  45.0  10.0  0.0  51.0  10.0  ...   

     X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  X_2868  X_2869  \
0       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
1       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
2       NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
3     183.8   467.0  444.192308   423.0     NaN     NaN     NaN     NaN   
4     179.7   465.0  443.211539   423.0     NaN     NaN     NaN     NaN   
..      ...     ...         ...     ...     ...     ...     ...     ...   
305     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
306     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
307     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
308     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   
309     NaN     NaN         NaN     NaN     NaN     NaN     NaN     NaN   

     X_2870  X_2871  
0       NaN     NaN  
1       NaN     NaN  
2       NaN     NaN  
3       NaN     NaN  
4       NaN     NaN  
..      ...     ...  
305     NaN     NaN  
306     NaN     NaN  
307     NaN     NaN  
308     NaN     NaN  
309     NaN     NaN  

[310 rows x 2795 columns]

In [397]:
TT05 = test_data[(test_data['LINE'] == 'T050304')|(test_data['LINE'] == 'T050307')]
TT01 = test_data[(test_data['LINE'] == 'T010305')|(test_data['LINE'] == 'T010306')]
TT10 = test_data[(test_data['LINE'] == 'T100304')|(test_data['LINE'] == 'T100306')]

In [398]:
TT05.drop(['LINE'], axis = 1, inplace = True)
TT01.drop(['LINE'], axis = 1, inplace = True)
TT10.drop(['LINE'], axis = 1, inplace = True)

In [399]:
TT05.drop(T05_col, inplace = True, axis = 1)
TT01.drop(T01_col, inplace = True, axis = 1)
TT10.drop(T10_col, inplace = True, axis = 1)

In [400]:
TT05 = TT05.fillna(0)
TT01 = TT01.fillna(0)
TT10 = TT10.fillna(0)
TT05

PRODUCT_CODE    X_128    X_129    X_130    X_131  X_132  X_133  X_134  \
7               1  18031.0  18031.0      0.0      0.0   0.19   0.20   0.19   
8               1  18064.0  18064.0      0.0      0.0   0.19   0.20   0.19   
13              1      0.0      0.0   3370.0   3370.0   0.21   0.22   0.21   
14              1    295.0    295.0      0.0      0.0   0.19   0.21   0.19   
35              1   8632.0   8632.0      0.0      0.0   0.20   0.21   0.20   
36              1      0.0      0.0   4394.0   4394.0   0.21   0.22   0.21   
41              1  10712.0  10712.0      0.0      0.0   0.20   0.21   0.20   
42              1  10729.0  10729.0      0.0      0.0   0.20   0.21   0.19   
52              1  12261.0  12261.0      0.0      0.0   0.19   0.21   0.19   
53              1  12283.0  12283.0      0.0      0.0   0.20   0.21   0.20   
54              1  12305.0  12305.0      0.0      0.0   0.19   0.21   0.19   
61              1  17990.0  17990.0      0.0      0.0   0.20   0.21   0.20   
62              1      0.0      0.0    304.0   5134.0   0.21   0.22   0.21   
63              1      0.0      0.0    337.0   5167.0   0.21   0.22   0.21   
64              1  18026.0  18026.0      0.0      0.0   0.20   0.21   0.20   
65              1  18220.0  18220.0      0.0      0.0   0.20   0.21   0.20   
66              1  18514.0  18514.0      0.0      0.0   0.20   0.21   0.20   
130             1      0.0      0.0   7614.0  12445.0   0.21   0.22   0.20   
131             1      0.0      0.0   7644.0  12475.0   0.21   0.21   0.21   
132             1      0.0      0.0   7786.0  12616.0   0.21   0.22   0.21   
248             1      0.0      0.0  16202.0  21032.0   0.21   0.22   0.21   
249             1      0.0      0.0  16231.0  21062.0   0.21   0.22   0.21   
250             1      0.0      0.0  16282.0  21113.0   0.21   0.22   0.21   
251             1      0.0      0.0  16287.0  21118.0   0.21   0.22   0.21   
252             1      0.0      0.0  16292.0  21123.0   0.21   0.22   0.21   
253             1      0.0      0.0  16297.0  21128.0   0.21   0.22   0.21   
254             1      0.0      0.0  16702.0  21533.0   0.21   0.22   0.21   
255             1      0.0      0.0  16735.0  21565.0   0.21   0.22   0.21   
260             1      0.0      0.0  16808.0  21639.0   0.21   0.22   0.20   
263             1      0.0      0.0  17014.0  21844.0   0.20   0.22   0.20   
280             1      0.0      0.0  18533.0  23364.0   0.21   0.22   0.21   
281             1      0.0      0.0  18565.0  23395.0   0.21   0.22   0.21   
282             1      0.0      0.0  19029.0  23860.0   0.21   0.22   0.21   
283             1      0.0      0.0  19061.0  23892.0   0.21   0.22   0.21   
284             1      0.0      0.0  19591.0  24422.0   0.21   0.22   0.21   
285             1      0.0      0.0  19621.0  24452.0   0.21   0.22   0.21   
286             1      0.0      0.0  19646.0  24476.0   0.21   0.22   0.21   
292             1      0.0      0.0  20153.0  24984.0   0.21   0.22   0.21   
293             1      0.0      0.0  20183.0  25014.0   0.21   0.22   0.21   

     X_135  X_136  ...  X_2862  X_2863      X_2864  X_2865  X_2866  X_2867  \
7      0.2  354.0  ...   168.3   384.0  369.462963   354.0   57.74   52.51   
8      0.2  355.0  ...   169.8   384.0  370.259259   353.0   53.18   56.02   
13     0.2  230.0  ...   138.3   384.0  367.462963   353.0   51.89   55.25   
14     0.2   60.0  ...   139.5   384.0  369.377359   353.0   49.77   54.93   
35     0.2  249.0  ...   103.5   384.0  369.660377   352.0   55.22   58.14   
36     0.2   99.0  ...   129.7   384.0  368.207547   354.0    0.00    0.00   
41     0.2  293.0  ...   165.6   383.0  368.018519   352.0   49.67   45.00   
42     0.2  293.0  ...   171.8   384.0  368.452830   353.0   51.30   47.66   
52     0.2  330.0  ...   161.0   384.0  368.320755   353.0   54.06   51.18   
53     0.2  330.0  ...   175.1   384.0  361.226415   342.0   54.04   51.25   
54     0.2  330.0  ...   1

# Test T05

In [401]:
TT05_idx = TT05['PRODUCT_CODE'].index
TT05_idx = pd.DataFrame(TT05_idx, columns = ['index'])
TT05_idx

index
0       7
1       8
2      13
3      14
4      35
5      36
6      41
7      42
8      52
9      53
10     54
11     61
12     62
13     63
14     64
15     65
16     66
17    130
18    131
19    132
20    248
21    249
22    250
23    251
24    252
25    253
26    254
27    255
28    260
29    263
30    280
31    281
32    282
33    283
34    284
35    285
36    286
37    292
38    293

In [402]:
T_05c = T05_data.columns
T_05scaler = StandardScaler()
T_05scaled = T_05scaler.fit_transform(T05_data)
T05_data = pd.DataFrame(T_05scaled, columns = T_05c)
T05_data

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
0             0.0 -0.180370 -0.186560 -0.509145 -0.509145 -1.164247 -1.497746   
1             0.0 -0.989393 -0.995545  2.139491  2.139491  0.803495  0.667670   
2             0.0 -0.180163 -0.186353 -0.509145 -0.509145 -1.164247 -1.497746   
3             0.0 -0.989393 -0.995545  2.139758  2.139758  0.803495  0.667670   
4             0.0 -0.179956 -0.186145 -0.509145 -0.509145 -1.164247 -1.497746   
..            ...       ...       ...       ...       ...       ...       ...   
115           0.0  0.239104  0.232895 -0.509145 -0.509145 -1.164247 -1.497746   
116           0.0  0.242625  0.236416 -0.509145 -0.509145 -3.131989 -1.497746   
117           0.0  0.244903  0.238694 -0.509145 -0.509145 -1.164247 -1.497746   
118           0.0  0.544158  0.537935 -0.509145 -0.509145 -1.164247 -1.497746   
119           0.0  0.544468  0.538245 -0.509145 -0.509145 -1.164247 -1.497746   

        X_134         X_135     X_136  ...    X_2862    X_2863    X_2864  \
0   -0.912871 -2.775558e-17 -0.604357  ...  2.035623 -0.421350  0.124820   
1    0.912871 -2.775558e-17  0.076557  ...  1.739131 -0.421350 -0.068170   
2   -0.912871 -2.775558e-17 -0.604357  ... -0.013662 -0.421350 -0.211108   
3    0.912871 -2.775558e-17  0.080237  ...  0.012499 -0.120386  0.432112   
4   -2.738613 -2.775558e-17 -0.604357  ...  1.477520 -0.421350 -0.200399   
..        ...           ...       ...  ...       ...       ...       ...   
115 -0.912871 -2.775558e-17 -0.596995  ...  0.901976 -0.120386 -0.206776   
116 -2.738613 -2.775558e-17 -0.596995  ...  0.727569 -0.120386 -0.308806   
117 -0.912871 -2.775558e-17 -0.596995  ...  1.390316  2.889260  1.380698   
118 -0.912871 -2.775558e-17 -0.324630  ...  0.265390 -0.120386  0.646518   
119 -0.912871 -2.775558e-17 -0.324630  ... -0.789774 -0.421350 -0.315062   

       X_2865    X_2866    X_2867    X_2868    X_2869    X_2870    X_2871  
0    0.481750 -0.150142 -0.177590 -0.447943 -0.429001  0.882891 -2.171241  
1    0.481750 -0.172668 -0.086990  0.131727 -0.369150  0.675559 -2.171241  
2    0.481750 -0.157651 -0.376630  0.057737 -0.312173  0.905928 -2.171241  
3    0.481750 -0.230234 -0.258333  0.552703 -0.597061  0.644976 -2.171241  
4    0.203817 -0.182179 -0.130647  0.285319 -0.476881  0.851116 -2.171241  
..        ...       ...       ...       ...       ...       ...       ...  
115  0.203817 -2.119391 -2.097103 -2.109394 -2.061245 -2.206035  0.460566  
116  0.203817  0.427517  0.401690  0.566480  0.633466  0.448368  0.460566  
117  0.481750  0.469065  0.702597  0.677209  0.670334  0.303395  0.460566  
118  0.481750  0.356937  0.394179  0.487388  0.576967  0.434864  0.460566  
119  0.203817 -2.119391 -2.097103 -2.109394 -2.061245 -2.206035  0.460566  

[120 rows x 1988 columns]

In [403]:
TT05c = TT05.columns
TT05scaled = T_05scaler.transform(TT05)
TT05scaled
TT05 = pd.DataFrame(TT05scaled, columns = TT05c)
TT05

PRODUCT_CODE     X_128     X_129     X_130     X_131     X_132     X_133  \
0            0.0  0.877687  0.871448 -0.509145 -0.509145 -1.164247 -1.497746   
1            0.0  0.881104  0.874865 -0.509145 -0.509145 -1.164247 -1.497746   
2            0.0 -0.989393 -0.995545 -0.059568 -0.059568  2.771237  2.833086   
3            0.0 -0.958846 -0.965000 -0.509145 -0.509145 -1.164247  0.667670   
4            0.0 -0.095564 -0.101757 -0.509145 -0.509145  0.803495  0.667670   
5            0.0 -0.989393 -0.995545  0.077040  0.077040  2.771237  2.833086   
6            0.0  0.119817  0.113613 -0.509145 -0.509145  0.803495  0.667670   
7            0.0  0.121577  0.115373 -0.509145 -0.509145  0.803495  0.667670   
8            0.0  0.280213  0.274002 -0.509145 -0.509145 -1.164247  0.667670   
9            0.0  0.282491  0.276280 -0.509145 -0.509145  0.803495  0.667670   
10           0.0  0.284769  0.278558 -0.509145 -0.509145 -1.164247  0.667670   
11           0.0  0.873441  0.867203 -0.509145 -0.509145  0.803495  0.667670   
12           0.0 -0.989393 -0.995545 -0.468590  0.175760  2.771237  2.833086   
13           0.0 -0.989393 -0.995545 -0.464187  0.180162  2.771237  2.833086   
14           0.0  0.877169  0.870931 -0.509145 -0.509145  0.803495  0.667670   
15           0.0  0.897257  0.891018 -0.509145 -0.509145  0.803495  0.667670   
16           0.0  0.927701  0.921460 -0.509145 -0.509145  0.803495  0.667670   
17           0.0 -0.989393 -0.995545  0.506606  1.151089  2.771237  2.833086   
18           0.0 -0.989393 -0.995545  0.510608  1.155091  2.771237  0.667670   
19           0.0 -0.989393 -0.995545  0.529552  1.173901  2.771237  2.833086   
20           0.0 -0.989393 -0.995545  1.652294  2.296643  2.771237  2.833086   
21           0.0 -0.989393 -0.995545  1.656163  2.300646  2.771237  2.833086   
22           0.0 -0.989393 -0.995545  1.662966  2.307449  2.771237  2.833086   
23           0.0 -0.989393 -0.995545  1.663633  2.308116  2.771237  2.833086   
24           0.0 -0.989393 -0.995545  1.664300  2.308783  2.771237  2.833086   
25           0.0 -0.989393 -0.995545  1.664967  2.309450  2.771237  2.833086   
26           0.0 -0.989393 -0.995545  1.718997  2.363480  2.771237  2.833086   
27           0.0 -0.989393 -0.995545  1.723399  2.367749  2.771237  2.833086   
28           0.0 -0.989393 -0.995545  1.733138  2.377621  2.771237  2.833086   
29           0.0 -0.989393 -0.995545  1.760619  2.404969  0.803495  2.833086   
30           0.0 -0.989393 -0.995545  1.963263  2.607745  2.771237  2.833086   
31           0.0 -0.989393 -0.995545  1.967532  2.611881  2.771237  2.833086   
32           0.0 -0.989393 -0.995545  2.029432  2.673915  2.771237  2.833086   
33           0.0 -0.989393 -0.995545  2.033701  2.678184  2.771237  2.833086   
34           0.0 -0.989393 -0.995545  2.104406  2.748889  2.771237  2.833086   
35           0.0 -0.989393 -0.995545  2.108408  2.752891  2.771237  2.833086   
36           0.0 -0.989393 -0.995545  2.111743  2.756093  2.771237  2.833086   
37           0.0 -0.989393 -0.995545  2.179380  2.823863  2.771237  2.833086   
38           0.0 -0.989393 -0.995545  2.183382  2.827865  2.771237  2.833086   

       X_134         X_135     X_136  ...    X_2862    X_2863    X_2864  \
0  -0.912871 -2.775558e-17 -0.140599  ...  0.230508 -0.120386  0.526561   
1  -0.912871 -2.775558e-17 -0.136919  ...  0.361314 -0.120386  0.800766   
2   2.738613 -2.775558e-17 -0.596995  ... -2.385600 -0.120386 -0.162138   
3  -0.912871 -2.775558e-17 -1.222700  ... -2.280956 -0.120386  0.497083   
4   0.912871 -2.775558e-17 -0.527064  ... -5.420285 -0.120386  0.594541   
5   2.738613 -2.775558e-17 -1.079156  ... -3.135551 -0.120386  0.094259   
6   0.912871 -2.775558e-17 -0.365117  ... -0.004942 -0.421350  0.029167   
7  -0.912871 -2.775558e-17 -0.365117  ...  0.535721 -0.120386  0.178722   
8  -0.912871 -2.775558e-17 -0.228934  ... -0.406078 -0.120386  0.133242   
9   0.912871 -2.775558e-17 -0.228934  ...  0.823493 -

In [404]:
TT05 = pd.concat([TT05_idx, TT05], axis = 1)
TT05 = TT05.set_index('index')

# Test T01

In [405]:
TT01_idx = TT01['PRODUCT_CODE'].index
TT01_idx = pd.DataFrame(TT01_idx, columns = ['index'])
TT01_idx

index
0       3
1       4
2       5
3       6
4       9
5      10
6      11
7      12
8      37
9      38
10     39
11     40
12     71
13     72
14     79
15     86
16     87
17     88
18     89
19    109
20    114
21    115
22    116
23    117
24    128
25    129
26    141
27    142

In [406]:
T_01c = T01_data.columns
T_01scaler = StandardScaler()
T_01scaled = T_01scaler.fit_transform(T01_data)
T01_data = pd.DataFrame(T_01scaled, columns = T_01c)
T01_data

PRODUCT_CODE     X_246     X_247     X_248  X_249     X_250     X_251  \
0             0.0 -0.383751 -1.444519  1.627125    0.0  1.343260 -0.736647   
1             0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.012325   
2             0.0  2.647096  0.739187  1.728952    0.0  1.343260 -0.736647   
3             0.0 -0.383751 -0.716617  1.762894    0.0  1.343260 -0.736647   
4             0.0 -0.383751  1.467090 -0.816720    0.0 -0.744457  1.167789   
..            ...       ...       ...       ...    ...       ...       ...   
124           0.0 -0.383751 -0.352666  1.593183    0.0 -0.744457 -0.736647   
125           0.0  0.626531 -0.352666 -0.816720    0.0 -0.744457  1.634182   
126           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457  1.634182   
127           0.0 -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.522884   
128           0.0 -0.383751  0.739187  0.252462    0.0  1.343260 -0.736647   

     X_252     X_253     X_254  ...    X_2856    X_2857    X_2858    X_2859  \
0      0.0  0.862116  0.918073  ... -0.460967 -0.947393 -1.614798 -1.613758   
1      0.0 -1.159937 -1.089239  ... -0.853081 -0.902251 -0.482382  0.021791   
2      0.0  0.862116  0.918073  ... -0.835258  0.677709  0.312177 -0.804502   
3      0.0  0.862116  0.918073  ... -0.615436 -0.608830 -0.576879 -0.233763   
4      0.0 -1.159937 -1.089239  ... -0.692671 -0.285314 -0.340790 -0.344503   
..     ...       ...       ...  ...       ...       ...       ...       ...   
124    0.0  0.862116  0.918073  ...  0.246027  0.188674  0.191572  0.481790   
125    0.0 -1.159937 -1.089239  ...  1.796661  1.776158  2.038027  1.725489   
126    0.0 -1.159937 -1.089239  ...  1.737250  1.467689  2.051754  2.526227   
127    0.0 -1.159937 -1.089239  ...  1.083726  0.730375  1.139129  1.495490   
128    0.0  0.862116  0.918073  ...  1.143137  1.294646  1.484418  1.759563   

       X_2860    X_2861    X_2862    X_2863    X_2864    X_2865  
0    0.587225  0.286139 -0.107506 -1.780047 -1.530483 -1.244903  
1   -0.057559  0.234620 -0.053298 -1.780047 -1.630148 -1.244903  
2    1.262234  1.681451  1.862054 -1.780047 -1.694963 -1.244903  
3   -0.259054 -0.381828 -0.631517 -1.780047 -1.593852 -0.977026  
4   -0.692268 -0.435401 -0.252061 -1.780047 -1.687185 -1.244903  
..        ...       ...       ...       ...       ...       ...  
124  1.010365  1.320037  1.094107  0.765696  0.612538  0.630239  
125  1.876793  1.949674  1.862054  0.765696  0.459476  0.228423  
126  1.141337  1.305980  1.500667  0.638409  0.044413  0.094484  
127  2.471204  2.404982  2.151164  0.765696  0.969268  1.299932  
128  0.970066  1.546804  1.410321  1.529419  1.203548  1.299932  

[129 rows x 895 columns]

In [407]:
TT01c = TT01.columns
TT01scaled = T_01scaler.transform(TT01)
TT01 = pd.DataFrame(TT01scaled, columns = TT01c)
TT01

PRODUCT_CODE      X_246     X_247     X_248  X_249     X_250     X_251  \
0            0.0  -0.383751  0.739187 -0.816720    0.0 -0.744457 -0.017625   
1            0.0   0.626531  1.467090  0.693712    0.0  1.343260 -0.736647   
2            0.0   0.626531 -0.352666  0.744625    0.0  1.343260 -0.736647   
3            0.0  -0.383751  0.739187 -0.816720    0.0 -0.744457  0.040674   
4            0.0  -0.383751 -0.716617  0.846452    0.0 -0.744457 -0.736647   
5            0.0  -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
6            0.0  -0.383751  1.467090 -0.816720    0.0 -0.744457  0.293303   
7            0.0   0.626531 -0.716617  0.965250    0.0 -0.744457 -0.736647   
8            0.0  -0.383751  1.103139 -0.579124    0.0  1.343260 -0.736647   
9            0.0   0.626531 -1.080568 -0.816720    0.0 -0.744457  1.867378   
10           0.0   0.626531  0.011285 -0.460326    0.0  1.343260 -0.736647   
11           0.0   0.626531  0.739187 -0.816720    0.0 -0.744457  2.003409   
12           0.0   0.626531 -0.716617 -0.816720    0.0 -0.744457 -0.620049   
13           0.0   0.626531  2.194992  0.676741    0.0  1.343260 -0.736647   
14           0.0  -0.383751 -0.352666  0.761597    0.0  1.343260 -0.736647   
15           0.0  -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.289688   
16           0.0  -0.383751  0.375236  1.067077    0.0  1.343260 -0.736647   
17           0.0  15.780762 -0.352666 -0.816720    0.0 -0.744457 -0.289688   
18           0.0   0.626531 -0.716617 -0.816720    0.0 -0.744457 -0.289688   
19           0.0   2.647096  2.194992  1.338615    0.0  1.343260 -0.736647   
20           0.0  -0.383751  1.467090  1.389529    0.0  1.343260 -0.736647   
21           0.0   0.626531  0.739187  1.389529    0.0  1.343260 -0.736647   
22           0.0   0.626531 -0.352666 -0.816720    0.0 -0.744457  0.098973   
23           0.0  -0.383751 -1.080568 -0.816720    0.0 -0.744457  0.098973   
24           0.0  -0.383751  1.467090  1.610154    0.0  1.343260 -0.736647   
25           0.0   0.626531  0.739187  1.610154    0.0  1.343260 -0.736647   
26           0.0  -0.383751 -1.080568 -0.816720    0.0 -0.744457  0.604232   
27           0.0   0.626531 -1.444519 -0.816720    0.0 -0.744457  0.604232   

    X_252     X_253     X_254  ...    X_2856    X_2857    X_2858    X_2859  \
0     0.0 -1.159937 -1.089239  ... -1.512546  0.188674 -0.748433 -2.175978   
1     0.0  0.862116  0.918073  ... -0.567907  2.189957  0.214230 -1.111167   
2     0.0  0.862116  0.918073  ... -1.435312 -0.608830 -1.526400 -2.261163   
3     0.0 -1.159937 -1.089239  ... -2.730477 -1.511665 -2.283586 -4.671895   
4     0.0  0.862116  0.918073  ... -0.971904 -0.428263 -0.049173  0.209198   
5     0.0 -1.159937 -1.089239  ... -1.066962 -0.014464 -1.249747 -1.341166   
6     0.0 -1.159937 -1.089239  ... -0.781788 -0.962440 -1.787252 -2.440051   
7     0.0  0.862116  0.918073  ... -1.274901  0.421906 -1.534908 -2.005608   
8     0.0  0.862116  0.918073  ... -0.781788  1.731016 -0.361354 -1.383759   
9     0.0 -1.159937 -1.089239  ... -1.173902 -1.022629 -2.578014 -3.607084   
10    0.0  0.862116  0.918073  ... -1.566016 -0.307885 -2.227375 -3.368566   
11    0.0 -1.159937 -1.089239  ... -1.209549 -0.586259 -1.837235 -2.704124   
12    0.0 -1.159937 -1.089239  ... -1.215490 -0.059606 -0.523402 -0.881168   
13    0.0  0.862116  0.918073  ... -1.150138  0.745422 -0.373909 -2.746717   
14    0.0  0.862116  0.918073  ... -0.312439 -0.842062 -1.430688 -2.831902   
15    0.0 -1.159937 -1.089239  ... -1.435312  1.016272  0.122881 -1.162278   
16    0.0  0.862116  0.918073  ... -1.892778  2.220052  1.787657 -0.114504   
17    0.0 -1.159937 -1.089239  ...  2.117482  8.276567  7.594854  6.010288   
18    0.0 -1.159937 -1.089239  ...  0.370791  1.573020  0.452142  0.038828   
19    0.0  0.862116  0.918073  ...  0.139087  4.447044  4.187928  3.778444   
20    0.0  0.862116  0.918073  ... -0.847140  2.904701  1.924861  0.285865   
21    0.0  0.862116  0.91

In [408]:
TT01 = pd.concat([TT01_idx, TT01], axis = 1)
TT01 = TT01.set_index('index')
TT01

PRODUCT_CODE      X_246     X_247     X_248  X_249     X_250     X_251  \
index                                                                           
3               0.0  -0.383751  0.739187 -0.816720    0.0 -0.744457 -0.017625   
4               0.0   0.626531  1.467090  0.693712    0.0  1.343260 -0.736647   
5               0.0   0.626531 -0.352666  0.744625    0.0  1.343260 -0.736647   
6               0.0  -0.383751  0.739187 -0.816720    0.0 -0.744457  0.040674   
9               0.0  -0.383751 -0.716617  0.846452    0.0 -0.744457 -0.736647   
10              0.0  -0.383751 -0.352666 -0.816720    0.0 -0.744457  0.157272   
11              0.0  -0.383751  1.467090 -0.816720    0.0 -0.744457  0.293303   
12              0.0   0.626531 -0.716617  0.965250    0.0 -0.744457 -0.736647   
37              0.0  -0.383751  1.103139 -0.579124    0.0  1.343260 -0.736647   
38              0.0   0.626531 -1.080568 -0.816720    0.0 -0.744457  1.867378   
39              0.0   0.626531  0.011285 -0.460326    0.0  1.343260 -0.736647   
40              0.0   0.626531  0.739187 -0.816720    0.0 -0.744457  2.003409   
71              0.0   0.626531 -0.716617 -0.816720    0.0 -0.744457 -0.620049   
72              0.0   0.626531  2.194992  0.676741    0.0  1.343260 -0.736647   
79              0.0  -0.383751 -0.352666  0.761597    0.0  1.343260 -0.736647   
86              0.0  -0.383751 -0.716617 -0.816720    0.0 -0.744457 -0.289688   
87              0.0  -0.383751  0.375236  1.067077    0.0  1.343260 -0.736647   
88              0.0  15.780762 -0.352666 -0.816720    0.0 -0.744457 -0.289688   
89              0.0   0.626531 -0.716617 -0.816720    0.0 -0.744457 -0.289688   
109             0.0   2.647096  2.194992  1.338615    0.0  1.343260 -0.736647   
114             0.0  -0.383751  1.467090  1.389529    0.0  1.343260 -0.736647   
115             0.0   0.626531  0.739187  1.389529    0.0  1.343260 -0.736647   
116             0.0   0.626531 -0.352666 -0.816720    0.0 -0.744457  0.098973   
117             0.0  -0.383751 -1.080568 -0.816720    0.0 -0.744457  0.098973   
128             0.0  -0.383751  1.467090  1.610154    0.0  1.343260 -0.736647   
129             0.0   0.626531  0.739187  1.610154    0.0  1.343260 -0.736647   
141             0.0  -0.383751 -1.080568 -0.816720    0.0 -0.744457  0.604232   
142             0.0   0.626531 -1.444519 -0.816720    0.0 -0.744457  0.604232   

       X_252     X_253     X_254  ...    X_2856    X_2857    X_2858    X_2859  \
index                             ...                                           
3        0.0 -1.159937 -1.089239  ... -1.512546  0.188674 -0.748433 -2.175978   
4        0.0  0.862116  0.918073  ... -0.567907  2.189957  0.214230 -1.111167   
5        0.0  0.862116  0.918073  ... -1.435312 -0.608830 -1.526400 -2.261163   
6        0.0 -1.159937 -1.089239  ... -2.730477 -1.511665 -2.283586 -4.671895   
9        0.0  0.862116  0.918073  ... -0.971904 -0.428263 -0.049173  0.209198   
10       0.0 -1.159937 -1.089239  ... -1.066962 -0.014464 -1.249747 -1.341166   
11       0.0 -1.159937 -1.089239  ... -0.781788 -0.962440 -1.787252 -2.440051   
12       0.0  0.862116  0.918073  ... -1.274901  0.421906 -1.534908 -2.005608   
37       0.0  0.862116  0.918073  ... -0.781788  1.731016 -0.361354 -1.383759   
38       0.0 -1.159937 -1.089239  ... -1.173902 -1.022629 -2.578014 -3.607084   
39       0.0  0.862116  0.918073  ... -1.566016 -0.307885 -2.227375 -3.368566   
40       0.0 -1.159937 -1.089239  ... -1.209549 -0.586259 -1.837235 -2.704124   
71       0.0 -1.159937 -1.089239  ... -1.215490 -0.059606 -0.523402 -0.881168   
72       0.0  0.862116  0.918073  ... -1.150138  0.745422 -0.373909 -2.746717   
79       0.0  0.862116  0.918073  ... -0.312439 -0.842062 -1.430688 -2.831902   
86       0.0 -1.159937 -1.089239  ... -1.435312  1.016272  0.122881 -1.162278   
87       0.0  0.862116  0.918073  ... -1.892778  2.220052  1.787657 -0.114504   
88       0.0 -1.159937 -1.089239  ...

# Test T10

In [409]:
TT10_idx = TT10['PRODUCT_CODE'].index
TT10_idx = pd.DataFrame(TT10_idx, columns = ['index'])
TT10_idx

index
0        0
1        1
2        2
3       15
4       16
..     ...
238    305
239    306
240    307
241    308
242    309

[243 rows x 1 columns]

In [410]:
T_10c = T10_data.columns
T_10scaler = StandardScaler()
T_10scaled = T_10scaler.fit_transform(T10_data)
T10_data = pd.DataFrame(T_10scaled, columns = T_10c)
T10_data

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
0       -0.132260 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
1       -0.132260 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
2       -0.132260 -0.069603  0.457558  0.0  0.0  1.243964  0.0 -0.870577   
3       -0.132260 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  1.190073   
4       -0.132260 -0.069603  1.188953  0.0  0.0  1.243964  0.0 -0.870577   
..            ...       ...       ...  ...  ...       ...  ...       ...   
344     -0.132260 -0.239475 -1.980425  0.0  0.0 -0.803882  0.0  0.274229   
345     -0.132260 -0.069603  0.701357  0.0  0.0 -0.803882  0.0 -0.870577   
346     -0.132260 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  0.274229   
347      7.560864  6.385512 -0.273837  0.0  0.0  1.243964  0.0 -0.870577   
348      7.560864  3.157954 -1.980425  0.0  0.0 -0.803882  0.0  2.792801   

          X_8       X_9  ...      X_924      X_925      X_926      X_927  \
0   -0.226285 -0.997139  ...  -0.005131   0.278454   0.389930   0.438042   
1   -0.226285 -0.997139  ... -16.700869 -17.224533 -17.459659 -16.729021   
2   -0.226285 -0.997139  ...   0.507840  -0.334366   0.031056   0.438042   
3   -0.226285  1.002869  ...  -0.547137  -0.183849  -0.306945  -0.062522   
4   -0.226285 -0.997139  ...   0.517519   0.117185   0.254071   0.233266   
..        ...       ...  ...        ...        ...        ...        ...   
344 -0.226285  1.002869  ...   0.430410  -0.065586   0.110887   0.073996   
345 -0.226285 -0.997139  ...  -0.101917  -0.388122  -0.143620   0.062619   
346 -0.226285  1.002869  ...   0.023906   0.106434   0.185958   0.221890   
347 -0.226285 -0.997139  ...   1.611211   2.073907   2.201145   2.451674   
348 -0.226285  1.002869  ...   1.514424   1.364327   1.508299   1.598440   

         X_928      X_929      X_930      X_931      X_932      X_933  
0     0.207541   0.177997  -0.040715   0.134006   0.100241   0.036419  
1   -18.026231 -18.033575 -17.957129 -18.600584 -18.606323 -18.605157  
2     0.263473   0.270066   0.453531   0.134006   0.116251   0.036419  
3     0.263473   0.432794   0.515312   0.134006   0.125228   0.177643  
4     0.263473   0.343936   0.453531   0.134006   0.071363   0.036419  
..         ...        ...        ...        ...        ...        ...  
344   0.207541   0.424229   0.453531  -0.002743   0.039942   0.036419  
345   0.207541   0.365347   0.453531  -0.002743  -0.013923   0.036419  
346   0.263473   0.417806   0.453531  -0.002743  -0.027389   0.036419  
347  -0.072118  -0.190282  -0.102496  -0.002743   0.049219   0.036419  
348   0.207541  -0.085365  -0.102496  -0.002743   0.012112   0.036419  

[349 rows x 678 columns]

In [411]:
TT10c = TT10.columns
TT10scaled = T_10scaler.transform(TT10)
TT10 = pd.DataFrame(TT10scaled, columns = TT10c)
TT10

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
0        -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  0.503190   
1        -0.13226 -0.069603 -0.517635  0.0  0.0  1.243964  0.0 -0.870577   
2        -0.13226 -0.069603 -0.030038  0.0  0.0  1.243964  0.0 -0.870577   
3        -0.13226 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
4        -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  1.190073   
..            ...       ...       ...  ...  ...       ...  ...       ...   
238      -0.13226 -0.069603 -1.005231  0.0  0.0 -0.803882  0.0  0.503190   
239      -0.13226 -0.069603  0.213760  0.0  0.0  1.243964  0.0 -0.870577   
240      -0.13226 -0.069603 -1.005231  0.0  0.0 -0.803882  0.0  0.274229   
241      -0.13226 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  0.503190   
242      -0.13226 -0.069603 -1.980425  0.0  0.0 -0.803882  0.0  0.503190   

          X_8       X_9  ...     X_924     X_925     X_926     X_927  \
0   -0.226285  1.002869  ...  0.149728 -0.011829  0.064636  0.335654   
1   -0.226285 -0.997139  ... -0.266455 -0.560142 -0.638354 -0.642721   
2   -0.226285 -0.997139  ...  0.130371  0.278454  0.584747  1.143382   
3   -0.226285 -0.997139  ... -0.866534  1.106297  0.985002  0.631442   
4   -0.226285  1.002869  ... -0.150311  1.289068  1.349735  1.450546   
..        ...       ...  ...       ...       ...       ...       ...   
238 -0.226285  1.002869  ... -0.324527  0.170941 -0.175846 -0.472074   
239 -0.226285 -0.997139  ... -0.992357 -0.097839  0.116856  0.608689   
240 -0.226285  1.002869  ... -0.314849 -0.237605 -0.328184 -0.233168   
241 -0.226285  1.002869  ... -0.401957  0.256951 -0.082563 -0.585838   
242 -0.226285  1.002869  ... -0.334206  0.310707 -0.157536  0.005737   

        X_928     X_929     X_930     X_931     X_932     X_933  
0   -0.295846 -0.197776 -0.164277 -0.002743  0.017498  0.036419  
1    0.263473  0.372841  0.453531 -0.002743  0.048920  0.036419  
2    0.207541  0.003493 -0.102496 -0.002743 -0.000457  0.036419  
3   -0.295846 -0.165658 -0.102496 -0.002743  0.021987  0.036419  
4    0.095677 -0.083224 -0.102496 -0.002743 -0.004945  0.036419  
..        ...       ...       ...       ...       ...       ...  
238  0.207541  0.400676  0.206408 -0.002743 -0.040855  0.036419  
239  0.207541  0.089991 -0.040715 -0.002743  0.048920  0.036419  
240  0.039745 -0.108918 -0.102496 -0.002743 -0.013923  0.036419  
241  0.207541  0.044175 -0.040715 -0.002743 -0.049833  0.036419  
242  0.263473  0.111621 -0.102496 -0.002743 -0.038910  0.036419  

[243 rows x 678 columns]

In [412]:
TT10 = pd.concat([TT10_idx, TT10], axis = 1)
TT10 = TT10.set_index('index')
TT10

PRODUCT_CODE       X_1       X_2  X_3  X_4       X_5  X_6       X_7  \
index                                                                        
0          -0.13226 -0.069603 -0.273837  0.0  0.0 -0.803882  0.0  0.503190   
1          -0.13226 -0.069603 -0.517635  0.0  0.0  1.243964  0.0 -0.870577   
2          -0.13226 -0.069603 -0.030038  0.0  0.0  1.243964  0.0 -0.870577   
15         -0.13226 -0.069603  1.676550  0.0  0.0  1.243964  0.0 -0.870577   
16         -0.13226 -0.069603 -0.517635  0.0  0.0 -0.803882  0.0  1.190073   
...             ...       ...       ...  ...  ...       ...  ...       ...   
305        -0.13226 -0.069603 -1.005231  0.0  0.0 -0.803882  0.0  0.503190   
306        -0.13226 -0.069603  0.213760  0.0  0.0  1.243964  0.0 -0.870577   
307        -0.13226 -0.069603 -1.005231  0.0  0.0 -0.803882  0.0  0.274229   
308        -0.13226 -0.069603 -0.030038  0.0  0.0 -0.803882  0.0  0.503190   
309        -0.13226 -0.069603 -1.980425  0.0  0.0 -0.803882  0.0  0.503190   

            X_8       X_9  ...     X_924     X_925     X_926     X_927  \
index                      ...                                           
0     -0.226285  1.002869  ...  0.149728 -0.011829  0.064636  0.335654   
1     -0.226285 -0.997139  ... -0.266455 -0.560142 -0.638354 -0.642721   
2     -0.226285 -0.997139  ...  0.130371  0.278454  0.584747  1.143382   
15    -0.226285 -0.997139  ... -0.866534  1.106297  0.985002  0.631442   
16    -0.226285  1.002869  ... -0.150311  1.289068  1.349735  1.450546   
...         ...       ...  ...       ...       ...       ...       ...   
305   -0.226285  1.002869  ... -0.324527  0.170941 -0.175846 -0.472074   
306   -0.226285 -0.997139  ... -0.992357 -0.097839  0.116856  0.608689   
307   -0.226285  1.002869  ... -0.314849 -0.237605 -0.328184 -0.233168   
308   -0.226285  1.002869  ... -0.401957  0.256951 -0.082563 -0.585838   
309   -0.226285  1.002869  ... -0.334206  0.310707 -0.157536  0.005737   

          X_928     X_929     X_930     X_931     X_932     X_933  
index                                                              
0     -0.295846 -0.197776 -0.164277 -0.002743  0.017498  0.036419  
1      0.263473  0.372841  0.453531 -0.002743  0.048920  0.036419  
2      0.207541  0.003493 -0.102496 -0.002743 -0.000457  0.036419  
15    -0.295846 -0.165658 -0.102496 -0.002743  0.021987  0.036419  
16     0.095677 -0.083224 -0.102496 -0.002743 -0.004945  0.036419  
...         ...       ...       ...       ...       ...       ...  
305    0.207541  0.400676  0.206408 -0.002743 -0.040855  0.036419  
306    0.207541  0.089991 -0.040715 -0.002743  0.048920  0.036419  
307    0.039745 -0.108918 -0.102496 -0.002743 -0.013923  0.036419  
308    0.207541  0.044175 -0.040715 -0.002743 -0.049833  0.036419  
309    0.263473  0.111621 -0.102496 -0.002743 -0.038910  0.036419  

[243 rows x 678 columns]

In [413]:
from pycaret.regression import *
TT05_prediction = predict_model(T05_final_regression_model, data=TT05)
TT01_prediction = predict_model(T01_final_regression_model, data=TT01)
TT10_prediction = predict_model(T10_final_regression_model, data=TT10)

In [414]:
TT05_y_class = pd.DataFrame(TT05, columns = ['PRODUCT_CODE'])
TT05_idx = TT05_y_class.index
TT05_y_class = TT05_y_class.reset_index()
TT05_prediction = pd.concat([TT05_prediction, TT05_y_class], axis = 1)
TT05_prediction = TT05_prediction.set_index('index')
TT05_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)
TT05_prediction

X_128     X_129     X_130     X_131     X_132     X_133     X_134  \
index                                                                         
7      0.877687  0.871448 -0.509145 -0.509145 -1.164247 -1.497746 -0.912871   
8      0.881104  0.874865 -0.509145 -0.509145 -1.164247 -1.497746 -0.912871   
13    -0.989393 -0.995545 -0.059568 -0.059568  2.771237  2.833086  2.738613   
14    -0.958846 -0.965000 -0.509145 -0.509145 -1.164247  0.667670 -0.912871   
35    -0.095564 -0.101757 -0.509145 -0.509145  0.803495  0.667670  0.912871   
36    -0.989393 -0.995545  0.077040  0.077040  2.771237  2.833086  2.738613   
41     0.119817  0.113613 -0.509145 -0.509145  0.803495  0.667670  0.912871   
42     0.121577  0.115373 -0.509145 -0.509145  0.803495  0.667670 -0.912871   
52     0.280213  0.274002 -0.509145 -0.509145 -1.164247  0.667670 -0.912871   
53     0.282491  0.276280 -0.509145 -0.509145  0.803495  0.667670  0.912871   
54     0.284769  0.278558 -0.509145 -0.509145 -1.164247  0.667670 -0.912871   
61     0.873441  0.867203 -0.509145 -0.509145  0.803495  0.667670  0.912871   
62    -0.989393 -0.995545 -0.468590  0.175760  2.771237  2.833086  2.738613   
63    -0.989393 -0.995545 -0.464187  0.180162  2.771237  2.833086  2.738613   
64     0.877169  0.870931 -0.509145 -0.509145  0.803495  0.667670  0.912871   
65     0.897257  0.891018 -0.509145 -0.509145  0.803495  0.667670  0.912871   
66     0.927701  0.921460 -0.509145 -0.509145  0.803495  0.667670  0.912871   
130   -0.989393 -0.995545  0.506606  1.151089  2.771237  2.833086  0.912871   
131   -0.989393 -0.995545  0.510608  1.155091  2.771237  0.667670  2.738613   
132   -0.989393 -0.995545  0.529552  1.173901  2.771237  2.833086  2.738613   
248   -0.989393 -0.995545  1.652294  2.296643  2.771237  2.833086  2.738613   
249   -0.989393 -0.995545  1.656163  2.300646  2.771237  2.833086  2.738613   
250   -0.989393 -0.995545  1.662966  2.307449  2.771237  2.833086  2.738613   
251   -0.989393 -0.995545  1.663633  2.308116  2.771237  2.833086  2.738613   
252   -0.989393 -0.995545  1.664300  2.308783  2.771237  2.833086  2.738613   
253   -0.989393 -0.995545  1.664967  2.309450  2.771237  2.833086  2.738613   
254   -0.989393 -0.995545  1.718997  2.363480  2.771237  2.833086  2.738613   
255   -0.989393 -0.995545  1.723399  2.367749  2.771237  2.833086  2.738613   
260   -0.989393 -0.995545  1.733138  2.377621  2.771237  2.833086  0.912871   
263   -0.989393 -0.995545  1.760619  2.404969  0.803495  2.833086  0.912871   
280   -0.989393 -0.995545  1.963263  2.607745  2.771237  2.833086  2.738613   
281   -0.989393 -0.995545  1.967532  2.611881  2.771237  2.833086  2.738613   
282   -0.989393 -0.995545  2.029432  2.673915  2.771237  2.833086  2.738613   
283   -0.989393 -0.995545  2.033701  2.678184  2.771237  2.833086  2.738613   
284   -0.989393 -0.995545  2.104406  2.748889  2.771237  2.833086  2.738613   
285   -0.989393 -0.995545  2.108408  2.752891  2.771237  2.833086  2.738613   
286   -0.989393 -0.995545  2.111743  2.756093  2.771237  2.833086  2.738613   
292   -0.989393 -0.995545  2.179380  2.823863  2.771237  2.833086  2.738613   
293   -0.989393 -0.995545  2.183382  2.827865  2.771237  2.833086  2.738613   

              X_135     X_136     X_137  ...    X_2863    X_2864    X_2865  \
index                                    ...                                 
7     -2.775558e-17 -0.140599 -0.141132  ... -0.120386  0.526561  0.759683   
8     -2.775558e-17 -0.136919 -0.141132  ... -0.120386  0.800766  0.481750   
13    -2.775558e-17 -0.596995 -0.597860  ... -0.120386 -0.162138  0.481750   
14    -2.775558e-17 -1.222700 -1.224020  ... -0.120386  0.497083  0.481750   
35    -2.775558e-17 -0.527064 -0.527877  ... -0.120386  0.594541  0.203817   
36    -2.775558e-17 -1.079156 -1.080371  ... -0.120386  0.094259  0.759683   
41    -2.775558e-17 -0.365117 -0.365812  ... -0.421350  0.029167  0.203817   
42    -2.775558e-17 -0.365117 -0.365812  ... -0.120386  0.178722  0.

In [415]:
TT01_y_class = pd.DataFrame(TT01, columns = ['PRODUCT_CODE'])
TT01_idx = TT01_y_class.index
TT01_y_class = TT01_y_class.reset_index()
TT01_prediction = pd.concat([TT01_prediction, TT01_y_class], axis = 1)
TT01_prediction = TT01_prediction.set_index('index')
TT01_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [416]:
TT10_y_class = pd.DataFrame(TT10, columns = ['PRODUCT_CODE'])
TT10_idx = TT10_y_class.index
TT10_y_class = TT10_y_class.reset_index()
TT10_prediction = pd.concat([TT10_prediction, TT10_y_class], axis = 1)
TT10_prediction = TT10_prediction.set_index('index')
TT10_prediction.drop(['PRODUCT_CODE'], axis = 1, inplace = True)

In [417]:
from pycaret.classification import *

In [418]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas

index
7      0.526387
8      0.525968
13     0.530967
14     0.522659
35     0.520552
36     0.531087
41     0.527986
42     0.524635
52     0.523714
53     0.525836
54     0.524992
61     0.527783
62     0.529099
63     0.531405
64     0.523364
65     0.522933
66     0.522966
130    0.532463
131    0.532249
132    0.534837
248    0.536685
249    0.534248
250    0.534426
251    0.531174
252    0.533310
253    0.535244
254    0.533117
255    0.532975
260    0.539903
263    0.532396
280    0.536267
281    0.537421
282    0.533689
283    0.535974
284    0.533788
285    0.533752
286    0.534888
292    0.530340
293    0.534320
Name: prediction_label, dtype: float64

In [419]:
TT05_datas = TT05_prediction['prediction_label']
TT05_datas = pd.DataFrame(TT05_datas.values, columns = ['Y_Quality'])
TT05_datas

Y_Quality
0    0.526387
1    0.525968
2    0.530967
3    0.522659
4    0.520552
5    0.531087
6    0.527986
7    0.524635
8    0.523714
9    0.525836
10   0.524992
11   0.527783
12   0.529099
13   0.531405
14   0.523364
15   0.522933
16   0.522966
17   0.532463
18   0.532249
19   0.534837
20   0.536685
21   0.534248
22   0.534426
23   0.531174
24   0.533310
25   0.535244
26   0.533117
27   0.532975
28   0.539903
29   0.532396
30   0.536267
31   0.537421
32   0.533689
33   0.535974
34   0.533788
35   0.533752
36   0.534888
37   0.530340
38   0.534320

In [420]:
TT05y_idx= TT05_prediction.index
TT05y_idx = pd.DataFrame(TT05y_idx, columns = ['index'])
TT05_datas = pd.concat([TT05y_idx, TT05_datas], axis = 1)
TT05_datas = TT05_datas.set_index('index')
TT05_datas

Y_Quality
index           
7       0.526387
8       0.525968
13      0.530967
14      0.522659
35      0.520552
36      0.531087
41      0.527986
42      0.524635
52      0.523714
53      0.525836
54      0.524992
61      0.527783
62      0.529099
63      0.531405
64      0.523364
65      0.522933
66      0.522966
130     0.532463
131     0.532249
132     0.534837
248     0.536685
249     0.534248
250     0.534426
251     0.531174
252     0.533310
253     0.535244
254     0.533117
255     0.532975
260     0.539903
263     0.532396
280     0.536267
281     0.537421
282     0.533689
283     0.535974
284     0.533788
285     0.533752
286     0.534888
292     0.530340
293     0.534320

In [421]:
TT01_datas = TT01_prediction['prediction_label']
TT01_datas

index
3      0.525930
4      0.531475
5      0.532762
6      0.532295
9      0.532871
10     0.531897
11     0.533152
12     0.534695
37     0.515347
38     0.549804
39     0.524569
40     0.531722
71     0.514428
72     0.530456
79     0.531453
86     0.516856
87     0.532172
88     0.516459
89     0.526677
109    0.534264
114    0.534418
115    0.533832
116    0.526347
117    0.526373
128    0.529744
129    0.530422
141    0.526719
142    0.527566
Name: prediction_label, dtype: float64

In [422]:
TT01_datas = TT01_prediction['prediction_label']
TT01_datas = pd.DataFrame(TT01_datas.values, columns = ['Y_Quality'])
TT01_datas

Y_Quality
0    0.525930
1    0.531475
2    0.532762
3    0.532295
4    0.532871
5    0.531897
6    0.533152
7    0.534695
8    0.515347
9    0.549804
10   0.524569
11   0.531722
12   0.514428
13   0.530456
14   0.531453
15   0.516856
16   0.532172
17   0.516459
18   0.526677
19   0.534264
20   0.534418
21   0.533832
22   0.526347
23   0.526373
24   0.529744
25   0.530422
26   0.526719
27   0.527566

In [423]:
TT01y_idx= TT01_prediction.index
TT01y_idx = pd.DataFrame(TT01y_idx, columns = ['index'])
TT01_datas = pd.concat([TT01y_idx, TT01_datas], axis = 1)
TT01_datas = TT01_datas.set_index('index')
TT01_datas

Y_Quality
index           
3       0.525930
4       0.531475
5       0.532762
6       0.532295
9       0.532871
10      0.531897
11      0.533152
12      0.534695
37      0.515347
38      0.549804
39      0.524569
40      0.531722
71      0.514428
72      0.530456
79      0.531453
86      0.516856
87      0.532172
88      0.516459
89      0.526677
109     0.534264
114     0.534418
115     0.533832
116     0.526347
117     0.526373
128     0.529744
129     0.530422
141     0.526719
142     0.527566

In [424]:
TT10_datas = TT10_prediction['prediction_label']
TT10_datas

index
0      0.531921
1      0.529785
2      0.529687
15     0.521928
16     0.534509
         ...   
305    0.526751
306    0.528455
307    0.528008
308    0.527108
309    0.526912
Name: prediction_label, Length: 243, dtype: float64

In [425]:
TT10_datas = TT10_prediction['prediction_label']
TT10_datas = pd.DataFrame(TT10_datas.values, columns = ['Y_Quality'])
TT10_datas

Y_Quality
0     0.531921
1     0.529785
2     0.529687
3     0.521928
4     0.534509
..         ...
238   0.526751
239   0.528455
240   0.528008
241   0.527108
242   0.526912

[243 rows x 1 columns]

In [426]:
TT10y_idx= TT10_prediction.index
TT10y_idx = pd.DataFrame(TT10y_idx, columns = ['index'])
TT10_datas = pd.concat([TT10y_idx, TT10_datas], axis = 1)
TT10_datas = TT10_datas.set_index('index')
TT10_datas

Y_Quality
index           
0       0.531921
1       0.529785
2       0.529687
15      0.521928
16      0.534509
...          ...
305     0.526751
306     0.528455
307     0.528008
308     0.527108
309     0.526912

[243 rows x 1 columns]

In [427]:
TT05_predictions = predict_model(T05_final_classification_model, data=TT05_datas)
TT01_predictions = predict_model(T01_final_classification_model, data=TT01_datas)
TT10_predictions = predict_model(T10_final_classification_model, data=TT10_datas)

In [428]:
TT10_predictions['prediction_label'].value_counts()

1    199
2     26
0     18
Name: prediction_label, dtype: int64

In [429]:
TT05_idxf = TT05_datas.index
TT05_p = pd.DataFrame(TT05_idxf, columns = ['index'])
TT05_predictions = pd.concat([TT05_p, TT05_predictions], axis = 1)
TT05_predictions = TT05_predictions.set_index('index')
TT05_predictions

Y_Quality  prediction_label  prediction_score
index                                               
7       0.526387                 1            0.9980
8       0.525968                 1            0.9980
13      0.530967                 1            0.9980
14      0.522659                 0            0.9972
35      0.520552                 0            0.9972
36      0.531087                 1            0.9980
41      0.527986                 1            0.9980
42      0.524635                 0            0.9961
52      0.523714                 0            0.9972
53      0.525836                 1            0.9980
54      0.524992                 1            0.8367
61      0.527783                 1            0.9980
62      0.529099                 1            0.9980
63      0.531405                 1            0.9980
64      0.523364                 0            0.9972
65      0.522933                 0            0.9972
66      0.522966                 0            0.9972
130     0.532463                 1            0.9980
131     0.532249                 1            0.9980
132     0.534837                 1            0.9232
248     0.536685                 2            0.9973
249     0.534248                 1            0.9980
250     0.534426                 1            0.9916
251     0.531174                 1            0.9980
252     0.533310                 1            0.9980
253     0.535244                 2            0.9526
254     0.533117                 1            0.9980
255     0.532975                 1            0.9980
260     0.539903                 2            0.9973
263     0.532396                 1            0.9980
280     0.536267                 2            0.9973
281     0.537421                 2            0.9973
282     0.533689                 1            0.9980
283     0.535974                 2            0.9930
284     0.533788                 1            0.9980
285     0.533752                 1            0.9980
286     0.534888                 1            0.8968
292     0.530340                 1            0.9980
293     0.534320                 1            0.9980

In [430]:
TT01_idxf = TT01_datas.index
TT01_p = pd.DataFrame(TT01_idxf, columns = ['index'])
TT01_predictions = pd.concat([TT01_p, TT01_predictions], axis = 1)
TT01_predictions = TT01_predictions.set_index('index')
TT01_predictions

Y_Quality  prediction_label  prediction_score
index                                               
3       0.525930                 1            0.9805
4       0.531475                 1            0.9967
5       0.532762                 1            0.9915
6       0.532295                 1            0.9942
9       0.532871                 1            0.9915
10      0.531897                 1            0.9967
11      0.533152                 1            0.9910
12      0.534695                 1            0.9866
37      0.515347                 0            0.9776
38      0.549804                 2            0.9885
39      0.524570                 0            0.9776
40      0.531722                 1            0.9967
71      0.514428                 0            0.9776
72      0.530456                 1            0.9967
79      0.531453                 1            0.9967
86      0.516856                 0            0.9776
87      0.532172                 1            0.9942
88      0.516459                 0            0.9776
89      0.526677                 1            0.9835
109     0.534264                 1            0.9886
114     0.534418                 1            0.9886
115     0.533832                 1            0.9900
116     0.526347                 1            0.9835
117     0.526373                 1            0.9835
128     0.529744                 1            0.9967
129     0.530422                 1            0.9967
141     0.526719                 1            0.9858
142     0.527566                 1            0.9895

In [431]:
TT10_idxf = TT10_datas.index
TT10_p = pd.DataFrame(TT10_idxf, columns = ['index'])
TT10_predictions = pd.concat([TT10_p, TT10_predictions], axis = 1)
TT10_predictions = TT10_predictions.set_index('index')
TT10_predictions

Y_Quality  prediction_label  prediction_score
index                                               
0       0.531921                 1            0.5164
1       0.529785                 1            0.5164
2       0.529687                 1            0.5164
15      0.521928                 0            0.5107
16      0.534509                 1            0.4214
...          ...               ...               ...
305     0.526751                 1            0.5161
306     0.528455                 1            0.5164
307     0.528008                 1            0.5164
308     0.527108                 1            0.5164
309     0.526912                 1            0.5164

[243 rows x 3 columns]

In [432]:
final_test = pd.concat([TT05_predictions, TT01_predictions, TT10_predictions])
final_test

Y_Quality  prediction_label  prediction_score
index                                               
7       0.526387                 1            0.9980
8       0.525968                 1            0.9980
13      0.530967                 1            0.9980
14      0.522659                 0            0.9972
35      0.520552                 0            0.9972
...          ...               ...               ...
305     0.526751                 1            0.5161
306     0.528455                 1            0.5164
307     0.528008                 1            0.5164
308     0.527108                 1            0.5164
309     0.526912                 1            0.5164

[310 rows x 3 columns]

In [433]:
final_test = final_test.sort_index(ascending=True)
final_test['prediction_label']

index
0      1
1      1
2      1
3      1
4      1
      ..
305    1
306    1
307    1
308    1
309    1
Name: prediction_label, Length: 310, dtype: int32

In [434]:
#52
sample_submission = pd.read_csv('sample_submission.csv')
sample_submission['Y_Class'] = final_test['prediction_label']
display(sample_submission.head())
sample_submission.to_csv('line3_standard_regpyc_classpyc_fill0_submission.csv',index=False)

PRODUCT_ID  Y_Class
0   TEST_000        1
1   TEST_001        1
2   TEST_002        1
3   TEST_003        1
4   TEST_004        1

In [435]:
final_test['prediction_label'].value_counts()

1    247
2     33
0     30
Name: prediction_label, dtype: int64

In [436]:
np.array(final_test['prediction_label'])

array([1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 0, 1, 0, 1, 1, 0, 1,
       0, 0, 0, 0, 1, 0, 0, 1, 0, 1, 0, 1, 2, 0, 1, 0, 2, 0, 1, 1, 0, 1,
       1, 1, 1, 0, 1, 0, 1, 0, 0, 1, 1, 0, 1, 1, 0, 0, 0, 1, 1, 1, 0, 0,
       0, 1, 1, 1, 1, 0, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 0, 1,
       0, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 2, 1,
       2, 2, 1, 2, 2, 1, 1, 2, 1, 1, 1, 2, 1, 2, 1, 2, 1, 2, 1, 1, 1, 1,
       2, 1, 1, 1, 2, 1, 2, 2, 1, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 2, 1, 2,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 2, 1, 1, 1, 1, 2, 1, 1, 1, 1, 1, 1, 2, 1, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 2, 2, 1, 2, 1, 1,
       1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1, 1,